In [1]:
#Establishing connection to local Elasticsearch instance

from elasticsearch import Elasticsearch
ELASTIC_USER = "username"
ELASTIC_PASSWORD = 'password'
es = Elasticsearch(    ["http://localhost:9200"],    http_auth=(ELASTIC_USER, ELASTIC_PASSWORD), timeout=60)

print(es.ping())

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\4150790264.py:6: DeprecationWarning: The 'timeout' parameter is deprecated in favor of 'request_timeout'
  es = Elasticsearch(    ["http://localhost:9200"],    http_auth=(ELASTIC_USER, ELASTIC_PASSWORD), timeout=60)
C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\4150790264.py:6: DeprecationWarning: The 'http_auth' parameter is deprecated. Use 'basic_auth' or 'bearer_auth' parameters instead
  es = Elasticsearch(    ["http://localhost:9200"],    http_auth=(ELASTIC_USER, ELASTIC_PASSWORD), timeout=60)


True


In [46]:
#es.indices.delete(index = "jobs_prd")

ObjectApiResponse({'acknowledged': True})

In [12]:
#Reading file with pandas to perform early cleaning

import pandas as pd

In [3]:
jobs_true = pd.read_csv('postingstrue.csv')

In [13]:
import arrow
from datetime import datetime
import time

In [5]:
p1= jobs_true

In [6]:
#Converting fields in original csv to more useable object types before transferring to elasticsearch

p1['post_date'] = p1['original_listed_time'].apply(arrow.get)
p1['expiration_date'] = p1['expiry'].apply(arrow.get)

p1

job_id                     company_name  \
0           921716            Corcoran Sawyer Smith   
1          1829192                              NaN   
2         10998357           The National Exemplar    
3         23221523           Abrams Fensterman, LLP   
4         35982263                              NaN   
...            ...                              ...   
123844  3906267117                     Lozano Smith   
123845  3906267126                        Pinterest   
123846  3906267131                     EPS Learning   
123847  3906267195  Trelleborg Applied Technologies   
123848  3906267224                        Solugenix   

                                                    title  \
0                                   Marketing Coordinator   
1                       Mental Health Therapist/Counselor   
2                             Assitant Restaurant Manager   
3       Senior Elder Law / Trusts and Estates Associat...   
4                                      Service Technician   
...                                                   ...   
123844                   Title IX/Investigations Attorney   
123845       Staff Software Engineer, ML Serving Platform   
123846               Account Executive, Oregon/Washington   
123847                       Business Development Manager   
123848                  Marketing Social Media Specialist   

                                              description  max_salary  \
0       Job descriptionA leading real estate firm in N...        20.0   
1       At Aspen Therapy and Wellness , we are committ...        50.0   
2       The National Exemplar is accepting application...     65000.0   
3       Senior Associate Attorney - Elder Law / Trusts...    175000.0   
4       Looking for HVAC service tech with experience ...     80000.0   
...                                                   ...         ...   
123844  Our Walnut Creek office is currently seeking a...    195000.0   
123845  About Pinterest:\n\nMillions of people across ...         NaN   
123846  Company Overview\n\nEPS Learning is a leading ...         NaN   
123847  The Business Development Manager is a 'hunter'...         NaN   
123848  Marketing Social Media Specialist - $70k – $75...     75000.0   

       pay_period                 location  company_id  views  med_salary  \
0          HOURLY            Princeton, NJ   2774458.0   20.0         NaN   
1          HOURLY         Fort Collins, CO         NaN    1.0         NaN   
2          YEARLY           Cincinnati, OH  64896719.0    8.0         NaN   
3          YEARLY        New Hyde Park, NY    766262.0   16.0         NaN   
4          YEARLY           Burlington, IA         NaN    3.0         NaN   
...           ...                      ...         ...    ...         ...   
123844     YEARLY         Walnut Creek, CA     56120.0    1.0         NaN   
123845        NaN            United States   1124131.0    3.0         NaN   
123846        NaN              Spokane, WA  90552133.0    3.0         NaN   
123847        NaN     Texas, United States   2793699.0    4.0         NaN   
123848     YEARLY  San Juan Capistrano, CA     43325.0    2.0         NaN   

        ...              posting_domain sponsored  work_type  currency  \
0       ...                         NaN         0  FULL_TIME       USD   
1       ...                         NaN         0  FULL_TIME       USD   
2       ...                         NaN         0  FULL_TIME       USD   
3       ...                         NaN         0  FULL_TIME       USD   
4       ...                         NaN         0  FULL_TIME       USD   
...     ...                         ...       ...        ...       ...   
123844  ...                         NaN         0  FULL_TIME       USD   
123845  ...    www.pinterestcareers.com         0  FULL_TIME       NaN   
123846  ...  epsoperations.bamboohr.com         0  FULL_TIME       NaN   
123847  ...                         NaN         0  FULL_TIME       NaN   
12

In [ ]:
#converting time to format that is easier to map and query for into new field

In [44]:
p1['post_month'] = p1['original_listed_time'].apply(lambda x: arrow.get(x).format('MMMM YYYY'))

In [45]:
p1

job_id                     company_name  \
0           921716            Corcoran Sawyer Smith   
1          1829192                              NaN   
2         10998357           The National Exemplar    
3         23221523           Abrams Fensterman, LLP   
4         35982263                              NaN   
...            ...                              ...   
123844  3906267117                     Lozano Smith   
123845  3906267126                        Pinterest   
123846  3906267131                     EPS Learning   
123847  3906267195  Trelleborg Applied Technologies   
123848  3906267224                        Solugenix   

                                                    title  \
0                                   Marketing Coordinator   
1                       Mental Health Therapist/Counselor   
2                             Assitant Restaurant Manager   
3       Senior Elder Law / Trusts and Estates Associat...   
4                                      Service Technician   
...                                                   ...   
123844                   Title IX/Investigations Attorney   
123845       Staff Software Engineer, ML Serving Platform   
123846               Account Executive, Oregon/Washington   
123847                       Business Development Manager   
123848                  Marketing Social Media Specialist   

                                              description  max_salary  \
0       Job descriptionA leading real estate firm in N...        20.0   
1       At Aspen Therapy and Wellness , we are committ...        50.0   
2       The National Exemplar is accepting application...     65000.0   
3       Senior Associate Attorney - Elder Law / Trusts...    175000.0   
4       Looking for HVAC service tech with experience ...     80000.0   
...                                                   ...         ...   
123844  Our Walnut Creek office is currently seeking a...    195000.0   
123845  About Pinterest:\n\nMillions of people across ...         NaN   
123846  Company Overview\n\nEPS Learning is a leading ...         NaN   
123847  The Business Development Manager is a 'hunter'...         NaN   
123848  Marketing Social Media Specialist - $70k – $75...     75000.0   

       pay_period                 location  company_id  views  med_salary  \
0          HOURLY            Princeton, NJ   2774458.0   20.0         NaN   
1          HOURLY         Fort Collins, CO         NaN    1.0         NaN   
2          YEARLY           Cincinnati, OH  64896719.0    8.0         NaN   
3          YEARLY        New Hyde Park, NY    766262.0   16.0         NaN   
4          YEARLY           Burlington, IA         NaN    3.0         NaN   
...           ...                      ...         ...    ...         ...   
123844     YEARLY         Walnut Creek, CA     56120.0    1.0         NaN   
123845        NaN            United States   1124131.0    3.0         NaN   
123846        NaN              Spokane, WA  90552133.0    3.0         NaN   
123847        NaN     Texas, United States   2793699.0    4.0         NaN   
123848     YEARLY  San Juan Capistrano, CA     43325.0    2.0         NaN   

        ...  sponsored  work_type  currency  compensation_type  \
0       ...          0  FULL_TIME       USD        BASE_SALARY   
1       ...          0  FULL_TIME       USD        BASE_SALARY   
2       ...          0  FULL_TIME       USD        BASE_SALARY   
3       ...          0  FULL_TIME       USD        BASE_SALARY   
4       ...          0  FULL_TIME       USD        BASE_SALARY   
...     ...        ...        ...       ...                ...   
123844  ...          0  FULL_TIME       USD        BASE_SALARY   
123845  ...          0  FULL_TIME       NaN                NaN   
123846  ...          0  FULL_TIME       NaN                NaN   
123847  ...          0  FULL_TIME       NaN                NaN   
123848  ...          0  FULL_TIME       USD        BASE_SALARY   

        normalized_sala

In [14]:
#Saving cleaned file to new csv

p1.to_csv('jobs_prd.csv', index=False)

In [15]:
print(p1.keys())


Index(['job_id', 'company_name', 'title', 'description', 'max_salary',
       'pay_period', 'location', 'company_id', 'views', 'med_salary',
       'min_salary', 'formatted_work_type', 'applies', 'original_listed_time',
       'remote_allowed', 'job_posting_url', 'application_url',
       'application_type', 'expiry', 'closed_time',
       'formatted_experience_level', 'skills_desc', 'listed_time',
       'posting_domain', 'sponsored', 'work_type', 'currency',
       'compensation_type', 'normalized_salary', 'zip_code', 'fips',
       'post_date', 'expiration_date', 'post_month'],
      dtype='object')


In [47]:
#creating new elasticsearch index called 'jobs_prd' and indexing documents from csv file

import csv
import requests


url = 'http://localhost:9200/'  

def index_document(jobs_prd):
    response = requests.post(url + 'jobs_prd/_doc/', json=jobs_prd, auth=("username", "password"))
    if response.status_code == 201:
        pass
    else:
        print("Failed to index document.")
        print("Response:", response.text)


with open("jobs_prd.csv", "r", encoding="utf-8") as f1:
    print("YOUR DATA IS PROCESSING. DO NOT RERUN THE CODE")
    reader = csv.reader(f1)
    
    headers = next(reader)  
    
    for line in reader:
        if line and len(line) >= 28:
            jobs_prd = {
                    'job_id': line[0],
                    'company_name': line[1],
                    'title': line[2],
                    'description': line[3],
                    'max_salary': line[4],
                    'pay_period': line[5],
                    'location': line[6],
                    'company_id': line[7],
                    'views': line[8],
                    'med_salary': line[9],
                    'min_salary': line[10],
                    'formatted_work_type': line[11],
                    'applies': line[12],
                    'remote_allowed': line[14],
                    'job_posting_url': line[15],
                    'application_url': line[16],
                    'application_type': line[17],
                    'formatted_experience_level': line[20],
                    'skills_desc': line[21],
                    'posting_domain': line[23],
                    'sponsored': line[24],
                    'work_type': line[25],
                    'currency': line[26],
                    'compensation_type': line[27],
                    'post_date': line[31],
                    'expiration_date': line[32],
                    'post_month' : line[33]
            }
            index_document(jobs_prd)


YOUR DATA IS PROCESSING. DO NOT RERUN THE CODE


In [48]:
#calculate annual salary for all entries where 'salary' exists
#painless scripting

script = {
    "script": {
        "source": """
            // Initialize minSalary
            def minSalary = null;

            // Check if min_salary is a String and convert it if not empty
            if (ctx._source.min_salary instanceof String) {
                if (ctx._source.min_salary.length() > 0) {
                    try {
                        minSalary = Double.parseDouble(ctx._source.min_salary);
                    } catch (NumberFormatException e) {
                        // Handle cases where the string cannot be parsed
                        minSalary = null; // Set to null if parsing fails
                    }
                } else {
                    minSalary = null; // Set to null if the string is empty
                }
            } else if (ctx._source.min_salary instanceof Number) {
                minSalary = ((Number) ctx._source.min_salary).doubleValue();
            } else {
                return; // Exit if min_salary is neither a String nor a Number
            }

            // Calculate yearly_salary based on pay_period
            if (minSalary == null) {
                ctx._source.yearly_salary = null;
            } else if (ctx._source.pay_period == 'YEARLY') {
                ctx._source.yearly_salary = minSalary;
            } else if (ctx._source.pay_period == 'MONTHLY') {
                ctx._source.yearly_salary = minSalary * 12;
            } else {
                ctx._source.yearly_salary = minSalary * 1760;
            }
        """,
        "lang": "painless"
    },
    "query": {
        "match_all": {}  # Adjust this query to select specific documents if needed
    },
    "conflicts": "proceed"  # Allow the update to proceed even if there are version conflicts
}

# Execute the update_by_query request
try:
    response = es.update_by_query(index="jobs_prd", body=script)
    print("Update by Query Response:", response)
except exceptions.RequestError as e:
    print(f"RequestError: {e.info}")
except exceptions.ConnectionError as e:
    print(f"ConnectionError: {e}")
except Exception as e:
    print(f"An error occurred: {e}")

Update by Query Response: {'took': 21987, 'timed_out': False, 'total': 123849, 'updated': 123849, 'deleted': 0, 'batches': 124, 'version_conflicts': 0, 'noops': 0, 'retries': {'bulk': 0, 'search': 0}, 'throttled_millis': 0, 'requests_per_second': -1.0, 'throttled_until_millis': 0, 'failures': []}


In [15]:

from elasticsearch import Elasticsearch
from elasticsearch.helpers import bulk
from elasticsearch import helpers, Elasticsearch


In [3]:
#DATA PARSING---------------------------------------------------------------------------------------------------------

#make new feild 'state'
#fill 'state' with last two letters of 'location'
#painless scripting

index_name = 'jobs_prd'

# Define the update script
script = {
    "source": """
        if (ctx._source.containsKey('location') && ctx._source['location'] != null) {
            String location = ctx._source['location'];
            if (location.length() >= 2) {
                String stateAbbreviation = location.substring(location.length() - 2).toUpperCase();
                ctx._source.state = stateAbbreviation;
            } else {
                ctx._source.state = "Unknown";
            }
        }
    """,
    "lang": "painless"
}

# Search for documents that need to be updated
search_query = {
    "query": {
        "exists": {
            "field": "location"  # Adjust if the field name is different
        }
    }
}

# Scroll to retrieve all documents
scroll_size = 1000
scroll = '2m'
response = es.search(index=index_name, body=search_query, scroll=scroll, size=scroll_size)
scroll_id = response['_scroll_id']

# Process each batch of documentspostings
while True:
    bulk_updates = []
    for hit in response['hits']['hits']:
        doc_id = hit['_id']
        bulk_updates.append({
            "_op_type": "update",
            "_index": index_name,
            "_id": doc_id,
            "script": script
        })
    
    # Perform the bulk update
    if bulk_updates:
        helpers.bulk(es, bulk_updates)
    
    # Fetch the next batch
    response = es.scroll(scroll_id=scroll_id, scroll=scroll)
    scroll_id = response['_scroll_id']
    
    # Break the loop if no more documents
    if not response['hits']['hits']:
        break

# Clear the scroll context
es.clear_scroll(scroll_id=scroll_id)

print("Update completed.")

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\505961516.py:35: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  response = es.search(index=index_name, body=search_query, scroll=scroll, size=scroll_size)


Update completed.


In [111]:
#MILESTONE ---------------------------------------------------------------------------------------------------------

In [ ]:
#Additional cleaning to give leftover documents a proper 'state' field

In [6]:
NY_list = ['New York City', 'New York City Metropolitan Area', 
"New York City Metropolitan Area", 'New York, United States', '*NY', 'Albany, New York Metropolitan Area', 'New York, New York, United States', 'Brooklyn, New York, United States']

for i in NY_list:
    result = es.search(index='jobs_prd' , body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'NY'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("I'm walkin' here") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2684967246.py:5: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd' , body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


I'm walkin' here
I'm walkin' here
I'm walkin' here
I'm walkin' here
I'm walkin' here
I'm walkin' here
I'm walkin' here
I'm walkin' here


In [7]:
CA_list = ['California, United States', 'San Francisco Bay Area', 'Los Angeles Metropolitan Area', 'Los Angeles, California, United States', 'San Diego Metropolitan Area', 'Greater Sacramento']

for i in CA_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'CA'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print('success') 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3172027032.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success
success
success


In [8]:
TX_list = ['Texas, United States', 'Dallas-Fort Worth Metroplex', 'Greater Houston', 'Austin, Texas Metropolitan Area', 'San Antonio, Texas Metropolitan Area', 'TX']

for i in TX_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'TX'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3499725425.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success
success
success


In [9]:
DC_list = ['Washington DC-Baltimore Area', 'Washington District of Columbia', 'Washington DC, United States', 'District of Columbia, United States']

for i in DC_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'DC'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1884383762.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success


In [10]:
FL_list = ['Florida, United States', 'Tampa Metropolitan Area', 'Orlando Metropolitan Area', 'Greater Orlando', "Miami-Fort Lauderdale Area", 'Greater Tampa Bay Area', 'Gainesville Metropolitan Area']

for i in FL_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'FL'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3490606922.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success
success
success
success


In [11]:
GA_list = ['Atlanta Metropolitan Area', 'Georgia, United States']

for i in GA_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'GA'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2962619762.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success


In [12]:
NJ_list = ['New Jersey, United States']

for i in NJ_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'NJ'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1010732603.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success


In [13]:
NC_list = ['North Carolina, United States', 'Raleigh-Durham-Chapel Hill Area', 'Charlotte Metro']

for i in NC_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'NC'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\622122702.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success


In [14]:
IL_list = ['Illinois, United States', 'Greater Chicago Area']

for i in IL_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'IL'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1606999426.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success


In [16]:
KY_list = ['Kentucky, United States', 'Nashville Metropolitan Area']

for i in KY_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'KY'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2057190656.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [17]:
PA_list = ['Pennsylvania, United States', 'Pilidalphia Metropolitan Area']

for i in PA_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'PA'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3225158397.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success


In [18]:
OH_list = ['Ohio, United States', 'Columbus, Ohio Metropolitan Area', 'Cincinnati Metropolitan Area']

for i in OH_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'OH'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\467460788.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success


In [19]:
MA_list = ['Massachusetts, United States', 'Greater Boston']

for i in MA_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'MA'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1814170413.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success


In [20]:
CO_list = ['Colorado, United States', 'Denver Metropolitan Area', 'Aurora, Colorado, United States']

for i in CO_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'CO'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2012401044.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success


In [21]:
VA_list = ['Virginia, United States', 'VA']

for i in VA_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'VA'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\721836193.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success


In [22]:
AZ_list = ['Greater Phoenix Area', "Arizona, United States"]

for i in AZ_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'AZ'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2559186354.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success


In [23]:
MN_list = ['Greater Minneapolis-St. Paul Area', "Minnesota, United States"]

for i in MN_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'MN'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2319064627.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success


In [24]:
WI_list = [ "Wisconsin, United States"]

for i in WI_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'WI'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2563976664.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success


In [25]:
MO_list = [ "Missouri, United States", 'St Louis, Missouri, United States', 'Greater St. Louis', 'Greater Jefferson City Area', 'Greater Columbia, Missouri Area']

for i in MO_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'MO'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3838721361.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success
success


In [26]:
IN_list = ['Indiana, United States', 'Greater Indianapolis', 'Indianapolis Metropolitan Area']

for i in IN_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'IN'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\505478200.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success


In [27]:
MT_list = ['Montana, United States']

for i in MT_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'MT'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2451213138.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [28]:
NV_list = ['Nevada, United States', 'Las Vegas Metropolitan Area']

for i in NV_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'NV'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("Let's go gambing!") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3995757717.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


Let's go gambing!
Let's go gambing!


In [29]:
KS_list = ['Kansas, United States', 'Kansas City Metropolitan Area', 'Witchita Metropolitan Area', 'Wichita, Kansas Metropolitan Area']

for i in KS_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'KS'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3493204407.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success


In [30]:
MI_list = ['Michigan, United States', 'Detroit Metropolitan Area', 'Ann Aarbor Area', 'Lansing Metropolitan Area']

for i in MI_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'MI'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3501590905.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success


In [31]:
OR_list = ['Oregan, United States', 'Portland, Oregon Metropolitan Area', 'Portland Metropolitan Area', 'Oregon, United States']

for i in OR_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'OR'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1663277494.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success


In [32]:
WA_list = ['Washington, United States', 'Washington State, United States', 'Greater Seattle Area', 'Seattle Metropolitan Area', 'Seattle, Washington, United States']

for i in WA_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'WA'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3130339152.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success
success


In [33]:
UT_list = ['Utah, United States', 'Salt Lake City Metropolitan Area']

for i in UT_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'UT'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1433057872.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success


In [34]:
MD_list = ['Maryland, United States', 'Baltimore Metropolitan Area', 'Greater Baltimore Metropolitan Area', 'Annapolis Metropolitan Area', 'Annapolis, Maryland, United States']

for i in MD_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'MD'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2604944146.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success
success


In [35]:
AR_list = ['Arkansas, United States', 'Little Rock Metropolitan Area']

for i in AR_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'AR'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1175405674.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success


In [36]:
SC_list = ['South Carolina, United States']

for i in SC_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'SC'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\793832875.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success


In [37]:
TN_list = ['Tennessee, United States']

for i in TN_list:
    result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'TN'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2398081738.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success


In [39]:
# Making all documents with location "United States" have state "Unknown"
result = es.search(index= 'jobs_prd' , body={'query': {'match_phrase': {'location': 'United States'}}}, scroll='2m', size=10000)
hits = result['hits']['hits']

for hit in hits:
    document_id = hit['_id']          # Access the '_id' field
    #print(f"Document ID: {document_id}")
    es.update(index='jobs_prd', id= document_id, body={'doc': {'state': 'Remote'}})
    es.update(index='jobs_prd', id= document_id, body={'doc': {'region': 'Remote'}})

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\573078976.py:2: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index= 'jobs_prd' , body={'query': {'match_phrase': {'location': 'United States'}}}, scroll='2m', size=10000)


In [40]:
SE_list= ["AR", "LA", "MS", "AL", "TN", "KY", "WV", "FL", "GA", "SC", "NC", "VA", "DC"]
for i in SE_list:
    result = es.search(index='jobs_prd', body={'query': { 'bool': { 'must': [ {'match': {'state': i}}]}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd', id= document_id, body={'doc': {'region': 'Southeast'}})
        #print(es.search(index='jobs_test2', body={'query': {'match': {'state': i}}}))
print('Dixies') 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\203754399.py:3: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': { 'bool': { 'must': [ {'match': {'state': i}}]}}}, scroll='2m', size=10000)


Dixies


In [44]:
SW_list= ["AZ", "NM", "TX", "OK"]
for i in SW_list:
    result = es.search(index='jobs_prd', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd', id= document_id, body={'doc': {'region': 'Southwest'}})
        #print(es.search(index='jobs_test2', body={'query': {'match': {'state': i}}}))
print('Yeehaw') 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2839668368.py:3: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)


Yeehaw


In [45]:
W_list= ["WA", "OR", "ID", "MT", "WY", "CO", "UT", "NV", "CA", "HI", "AK"]
for i in W_list:
    result = es.search(index='jobs_prd', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd', id= document_id, body={'doc': {'region': 'West'}})
        #print(es.search(index='jobs_test2', body={'query': {'match': {'state': i}}}))
print('Liberals') 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2996782180.py:3: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)


Liberals


In [46]:
NE_list= ["ME", "VT", "NH", "MA", "CT", "RI", "NY", "PA", "NJ", "DE", "MD"]
for i in NE_list:
    result = es.search(index='jobs_prd', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd', id= document_id, body={'doc': {'region': 'Northeast'}})
        #print(es.search(index='jobs_test2', body={'query': {'match': {'state': i}}}))
print('Woke') 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2430050750.py:3: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)


Woke


In [47]:
MW_list= ["ND", "SD", "NE", "KS", "MN", "IA", "MO", "WI", "IL", "IN", "MI", "OH"]
for i in MW_list:
    result = es.search(index='jobs_prd', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd', id= document_id, body={'doc': {'region': 'Midwest'}})
        #print(es.search(index='jobs_test2', body={'query': {'match': {'state': i}}}))
print('Who?') 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1492121005.py:3: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)


Who?


In [41]:
#Categories start-------------------------------------------------------------------------------

In [69]:
#Painless scripting
index_name = 'jobs_prd'


update_body = {
    "script": {
        "source": "ctx._source.subcategory = 'Unknown'",
        "lang": "painless"
    },
    "query": {
        "match_all": {}
    }
}

try:
    response = es.update_by_query(index=index_name, body=update_body)
    print("Update by query response:", response)
except NotFoundError:
    print(f"Index {index_name} not found")
except Exception as e:
    print("An error occurred:", str(e))

Update by query response: {'took': 23563, 'timed_out': False, 'total': 123849, 'updated': 123849, 'deleted': 0, 'batches': 124, 'version_conflicts': 0, 'noops': 0, 'retries': {'bulk': 0, 'search': 0}, 'throttled_millis': 0, 'requests_per_second': -1.0, 'throttled_until_millis': 0, 'failures': []}


In [73]:
#UPDATES ALL ENTRIES TO HAVE CATEGORY : 'UNKNOWN'
#DOES NOT WORK AS INTENDED
exists_list = [
    'Service', 'Labor', 'General Management', 'Skilled Trade', 'IT', 
    'Scientific Development', 'Food Industry', 'Uncategorized Health', 
    'Marketing', 'Software', 'Sales', 'Medical', 'Retail', 'Finance', 
    'Entertainment', 'Education', 'Legal', 'Admin', 'Scientific Research', 
    'Data', 'Health Ally', 'Healthcare Management', 'Mental Health', 
    'Police and Security', 'Public Health'
]

# Convert the list to a set for faster lookup
exists_set = set(exists_list)

def update_documents_not_in_list():
    try:
        # Query to find documents where 'category' is not in the exists_list
        query = {
            "query": {
                "bool": {
                    "must_not": {
                        "terms": {
                            "category": list(exists_set)
                        }
                    }
                }
            }
        }

        # Perform the search with scroll
        result = es.search(
            index='jobs_prd',
            body=query,
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )
        
        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']
        
        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Unknown'
                es.update(index='jobs_prd', id=document_id, body={'doc': {'category': 'Unknown'}})
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)
        
        print("Completed processing all documents not in the list.")

    except Exception as e:
        print(f"An error occurred: {e}")

# Run the update function
update_documents_not_in_list()


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2091795832.py:31: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing all documents not in the list.


In [105]:
IT_list = ['IT ', 'Solutions Architect', 'System Architect', 'Artifical Intelligence', 'Programming', 'Full-stack', 'Back End Developer', 'Systems Admin', 'Cyber Security', 'Cybersecurity', 'Network', 'Systems Engineer', 'Chief Information Officer', ' CIO', 'Help Desk', 'Technical Support', 'Innovation Specialist', 'IoT ', 'Programmer']

for title in IT_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        #"must_not": {
                            #"match_phrase": {'category': 'IT'}
                        #}
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']

                # Update the document to set the category to 'IT'
                es.update(index='jobs_prd', id=document_id, body={'doc': {'category': 'IT'}, 'doc': {'subcategory': 'Unknown'}})
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        print(f"Completed processing for title: {title}")

        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)
    
    except Exception as e:
        print(f"An error occurred for title {title}: {e}")

print("All searches and updates completed.")

C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3699463710.py:6: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: IT 
Completed processing for title: Solutions Architect
Completed processing for title: System Architect
Completed processing for title: Artifical Intelligence
Completed processing for title: Programming
Completed processing for title: Full-stack
Completed processing for title: Back End Developer
Completed processing for title: Systems Admin
Completed processing for title: Cyber Security
Completed processing for title: Cybersecurity
Completed processing for title: Network
Completed processing for title: Systems Engineer
Completed processing for title: Chief Information Officer
Completed processing for title:  CIO
Completed processing for title: Help Desk
Completed processing for title: Technical Support
Completed processing for title: Innovation Specialist
Completed processing for title: IoT 
Completed processing for title: Programmer
All searches and updates completed.


In [104]:

IT_list = ['IT ', 'Solutions Architect', 'System Architect', 'Artifical Intelligence', 'Programming', 'Full-stack', 'Back End Developer', 'Systems Admin', 'Cyber Security', 'Cybersecurity', 'Network', 'Systems Engineer', 'Chief Information Officer', ' CIO', 'Help Desk', 'Technical Support', 'Innovation Specialist', 'IoT ', 'Programmer']

for title in IT_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']

                # Update the document to set the category to 'IT' and subcategory to 'Unknown'
                es.update(index='jobs_prd', id=document_id, body={
                    'doc': {
                        'category': 'IT',
                        'subcategory': 'Unknown'
                    }
                })
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        print(f"Completed processing for title: {title}")

        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)
    
    except Exception as e:
        print(f"An error occurred for title {title}: {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2198299653.py:6: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: IT 
Completed processing for title: Solutions Architect
Completed processing for title: System Architect
Completed processing for title: Artifical Intelligence
Completed processing for title: Programming
Completed processing for title: Full-stack
Completed processing for title: Back End Developer
Completed processing for title: Systems Admin
Completed processing for title: Cyber Security
Completed processing for title: Cybersecurity
Completed processing for title: Network
Completed processing for title: Systems Engineer
Completed processing for title: Chief Information Officer
Completed processing for title:  CIO
Completed processing for title: Help Desk
Completed processing for title: Technical Support
Completed processing for title: Innovation Specialist
Completed processing for title: IoT 
Completed processing for title: Programmer
All searches and updates completed.


In [107]:


Software_list = ['Software', '.NET Developer', 'Software Development', 'Java', 'C++']

for title in Software_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Software'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']  # Access the '_id' field

                # Update the document to set the category to 'IT' and subcategory to 'Software'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'IT',
                            'subcategory': 'Software'
                        }
                    }
                )

            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id,
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)
        
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title {title}: {e}")

print('All searches and updates completed.')


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1914237854.py:6: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Software
Completed processing for title: .NET Developer
Completed processing for title: Software Development
Completed processing for title: Java
Completed processing for title: C++
All searches and updates completed.


In [108]:

Data_list = ['Data', 'Database', 'Mongo DB']

for title in Data_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Data'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'IT' and subcategory to 'Data'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'IT',
                            'subcategory': 'Data'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)
        
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title {title}: {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3939312708.py:6: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Data
Completed processing for title: Database
Completed processing for title: Mongo DB
All searches and updates completed.


In [109]:

Admin_list = [
    'Administrative Assistant', 'Right-of-Way Agent', 'Associate Facilitator', 'secretary', 'Contract Coordinator', 'People Development',
    'Office Manager', 'Executive Assistant', 'Receptionist', 'Data Entry Clerk', 'Office Clerk', 'HR',
    'Administrative Coordinator', 'Planner', 'Office Administrator', 'Personal Assistant', 'Program Coordinator', 'Administrative Clerk',
    'Executive Secretary', 'Office Support Specialist', 'File Clerk', 'Human Resources', 'Human Resources Assistant', 'Outpatient Coordinator',
    'Payroll Clerk', 'Administrative Manager', 'Project Administrator', 'Accounts Receivable', 'Legal Secretary',
    'Facilities Coordinator', 'Eligibility Supervisor', 'Scheduler', 'Records Manager', 'Travel Coordinator', 'Front Desk',
    'Licensing Coordinator', 'Claims Examiner', 'Operations Coordinator', 'Purchasing Coordinator'
]

for title in Admin_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Admin'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Admin' and subcategory to 'Unknown'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Admin',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)
        
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title {title}: {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2674128176.py:14: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Administrative Assistant
Completed processing for title: Right-of-Way Agent
Completed processing for title: Associate Facilitator
Completed processing for title: secretary
Completed processing for title: Contract Coordinator
Completed processing for title: People Development
Completed processing for title: Office Manager
Completed processing for title: Executive Assistant
Completed processing for title: Receptionist
Completed processing for title: Data Entry Clerk
Completed processing for title: Office Clerk
Completed processing for title: HR
Completed processing for title: Administrative Coordinator
Completed processing for title: Planner
Completed processing for title: Office Administrator
Completed processing for title: Personal Assistant
Completed processing for title: Program Coordinator
Completed processing for title: Administrative Clerk
Completed processing for title: Executive Secretary
Completed processing for title: Office Support Specialist
C

In [110]:
Medical_list = [
    'Doctor', 'Nurse', 'Pharmacy', 'Veterinarian', 'Urology', 'Endodontist', 'Neuroscience', 'Surg', 'Vet', 
    'Medication Aide', 'X-Ray', 'Anesthesiology', 'Orthopedic', 'RN', 'Radiology', 'Home Health', 'Pharmacist', 
    'Physician', 'Dentist', 'Hygienist', 'Dosimetrist', 'Neurology', 'Audiologist', 'Oncology', 'Radiation Therapist',
    'Medical', 'Surgeon', 'Medicine Technologist', 'Anesthesiologist', 'Dental', 'Surgical', 'Neurological', 
    'Nursing', 'MRI', 'Veterinary', 'CMC', 'Radiologist', 'Medical Laboratory Technician', 'Paramedic', 'Patient Care', 
    'Phlebotomist', 'IR Tech', 'PM&R', 'Paraprofessional', 'Physical Therapy'
]

for title in Medical_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Medical'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Healthcare' and subcategory to 'Medical'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Healthcare',
                            'subcategory': 'Medical'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2668890306.py:13: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Doctor
Completed processing for title: Nurse
Completed processing for title: Pharmacy
Completed processing for title: Veterinarian
Completed processing for title: Urology
Completed processing for title: Endodontist
Completed processing for title: Neuroscience
Completed processing for title: Surg
Completed processing for title: Vet
Completed processing for title: Medication Aide
Completed processing for title: X-Ray
Completed processing for title: Anesthesiology
Completed processing for title: Orthopedic
Completed processing for title: RN
Completed processing for title: Radiology
Completed processing for title: Home Health
Completed processing for title: Pharmacist
Completed processing for title: Physician
Completed processing for title: Dentist
Completed processing for title: Hygienist
Completed processing for title: Dosimetrist
Completed processing for title: Neurology
Completed processing for title: Audiologist
Completed processing for title: Oncology


In [111]:

Healthcare_Management_list = [
    'Healthcare Administrator', 'Medical Office Manager', 'Management training', 'Head of Quality', 'VP', 'CFO', 'VP/CFO',
    'Clinical Manager', 'Health Services Manager', 'Practice Manager', 'Patient',
    'Medical Director', 'Health Information Manager', 'Hospital Administrator', 'Patient Service Representative', 'Credentialing Coordinator',
]

for title in Healthcare_Management_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Healthcare Management'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Healthcare' and subcategory to 'Healthcare Management'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Healthcare',
                            'subcategory': 'Healthcare Management'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\214966983.py:10: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Healthcare Administrator
Completed processing for title: Medical Office Manager
Completed processing for title: Management training
Completed processing for title: Head of Quality
Completed processing for title: VP
Completed processing for title: CFO
Completed processing for title: VP/CFO
Completed processing for title: Clinical Manager
Completed processing for title: Health Services Manager
Completed processing for title: Practice Manager
Completed processing for title: Patient
Completed processing for title: Medical Director
Completed processing for title: Health Information Manager
Completed processing for title: Hospital Administrator
Completed processing for title: Patient Service Representative
Completed processing for title: Credentialing Coordinator
All searches and updates completed.


In [112]:

Allied_Health_list = [
    'Physical Therapist', 'Occupational Therapist', 
    'Speech-Language Pathologist', 'Dietitian/Nutritionist', 
    'Respiratory Therapist', 'Health Educator', 
    'Certified Nursing Assistant (CNA)', 'Clinical Associate'
]

for title in Allied_Health_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Health Ally'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Healthcare' and subcategory to 'Health Ally'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Healthcare',
                            'subcategory': 'Health Ally'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3054644601.py:11: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Physical Therapist
Completed processing for title: Occupational Therapist
Completed processing for title: Speech-Language Pathologist
Completed processing for title: Dietitian/Nutritionist
Completed processing for title: Respiratory Therapist
Completed processing for title: Health Educator
Completed processing for title: Certified Nursing Assistant (CNA)
Completed processing for title: Clinical Associate
All searches and updates completed.


In [113]:
Public_Health_list = [
    'Epidemiologist', 'Public Health Analyst', 'Biostatistician', 
    'Health Research Scientist', 'Community Health Worker', 
    'Health Policy Analyst'
]

for title in Public_Health_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Public Health'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Healthcare' and subcategory to 'Public Health'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Healthcare',
                            'subcategory': 'Public Health'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


Completed processing for title: Epidemiologist
Completed processing for title: Public Health Analyst
Completed processing for title: Biostatistician
Completed processing for title: Health Research Scientist
Completed processing for title: Community Health Worker
Completed processing for title: Health Policy Analyst
All searches and updates completed.


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1117567723.py:10: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


In [116]:
Mental_Health_list = [
    'Psychologist', 'Counselor', 'Clinical Social Worker', 'Family Therapist',
    'Psychiatrist', 'Substance Abuse Counselor', 
    'Marriage and Family Therapist', 'Mental Health', 'PSYCHOLOGICAL'
]


for title in Mental_Health_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='job_postings_2',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Mental Health'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Healthcare' and subcategory to 'Mental Health'
                es.update(
                    index='job_postings_2', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Healthcare',
                            'subcategory': 'Mental Health'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


Completed processing for title: Psychologist
Completed processing for title: Counselor
Completed processing for title: Clinical Social Worker
Completed processing for title: Family Therapist
Completed processing for title: Psychiatrist
Completed processing for title: Substance Abuse Counselor
Completed processing for title: Marriage and Family Therapist
Completed processing for title: Mental Health
Completed processing for title: PSYCHOLOGICAL
All searches and updates completed.


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\841603101.py:11: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


In [123]:
Uncategorized_Health_list = [
    'Health', 
    'Healthcare', 
    'Medical'
]

for title in Uncategorized_Health_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Healthcare'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                print(document_id)
                # Update the document to set the category to 'Healthcare' and subcategory to 'Unknown'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Healthcare',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


Completed processing for title: Health
Completed processing for title: Healthcare
Completed processing for title: Medical
All searches and updates completed.


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\322519539.py:10: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


In [126]:
Sales_list = [
    'Sales Representative', 'Sales Manager', 'Account Manager', 'Sales Associate', 
    'Business Development Manager', 'Sales Director', 'Selling', 
    'Regional Sales Manager', 'Inside Sales Representative', 
    'Field Sales Representative', 'Sales Engineer', 'Sales Development Representative', 'Sales', 
    'Salesperson', 'Select Account Executive', 'Account Executive'
]

for title in Sales_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Sales'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Sales' and subcategory to 'Unknown'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Sales',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3195076841.py:12: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Sales Representative
Completed processing for title: Sales Manager
Completed processing for title: Account Manager
Completed processing for title: Sales Associate
Completed processing for title: Business Development Manager
Completed processing for title: Sales Director
Completed processing for title: Selling
Completed processing for title: Regional Sales Manager
Completed processing for title: Inside Sales Representative
Completed processing for title: Field Sales Representative
Completed processing for title: Sales Engineer
Completed processing for title: Sales Development Representative
Completed processing for title: Sales
Completed processing for title: Salesperson
Completed processing for title: Select Account Executive
Completed processing for title: Account Executive
All searches and updates completed.


In [127]:
Marketing_list = [
    'Marketing Manager', 'Marketing Director', 'Marketing Coordinator', 
    'Marketing Specialist', 'Content Marketing Manager', 
    'Digital Marketing Specialist', 'SEO Specialist', 'Social Media Manager', 
    'Brand Manager', 'Product Marketing Manager', 'Marketing', 'Search Planner'
]

for title in Marketing_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Marketing'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Marketing' and subcategory to 'Unknown'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Marketing',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1288867222.py:11: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Marketing Manager
Completed processing for title: Marketing Director
Completed processing for title: Marketing Coordinator
Completed processing for title: Marketing Specialist
Completed processing for title: Content Marketing Manager
Completed processing for title: Digital Marketing Specialist
Completed processing for title: SEO Specialist
Completed processing for title: Social Media Manager
Completed processing for title: Brand Manager
Completed processing for title: Product Marketing Manager
Completed processing for title: Marketing
Completed processing for title: Search Planner
All searches and updates completed.


In [128]:
Scientific_Research_list = [
    'Research Scientist', 'Biologist', 'Chemist', 'Physicist', 'Sterilization', 'Cytotechnologist', 'Specimen',
    'Data Scientist', 'Lab Technician', 'Biomedical Scientist', 'Behavior Technician',
    'Clinical Research Coordinator', 'Research Associate', 'Research Fellow', 'Ecologist', 'Lab', 'Laboratory', 'Scientist', 'Molecules',
]

for title in Scientific_Research_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Research'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'R&D' and subcategory to 'Research'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'R&D',
                            'subcategory': 'Research'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1501730906.py:10: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Research Scientist
Completed processing for title: Biologist
Completed processing for title: Chemist
Completed processing for title: Physicist
Completed processing for title: Sterilization
Completed processing for title: Cytotechnologist
Completed processing for title: Specimen
Completed processing for title: Data Scientist
Completed processing for title: Lab Technician
Completed processing for title: Biomedical Scientist
Completed processing for title: Behavior Technician
Completed processing for title: Clinical Research Coordinator
Completed processing for title: Research Associate
Completed processing for title: Research Fellow
Completed processing for title: Ecologist
Completed processing for title: Lab
Completed processing for title: Laboratory
Completed processing for title: Scientist
Completed processing for title: Molecules
All searches and updates completed.


In [129]:
Scientific_Development_list = [
    'Scientific Developer', 'Bioinformatics Specialist', 'Pharmaceutical Scientist', 
    'Research and Development (R&D) Scientist', 'Engineering Scientist', 
    'Technical Research Scientist', 'Scientific Programmer', 
    'Process Development Scientist', 'Applied Scientist', 'Development Chemist', 'Hazardous Waste Technician'
]

for title in Scientific_Development_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Development'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'R&D' and subcategory to 'Development'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'R&D',
                            'subcategory': 'Development'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1170313157.py:11: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Scientific Developer
Completed processing for title: Bioinformatics Specialist
Completed processing for title: Pharmaceutical Scientist
Completed processing for title: Research and Development (R&D) Scientist
Completed processing for title: Engineering Scientist
Completed processing for title: Technical Research Scientist
Completed processing for title: Scientific Programmer
Completed processing for title: Process Development Scientist
Completed processing for title: Applied Scientist
Completed processing for title: Development Chemist
Completed processing for title: Hazardous Waste Technician
All searches and updates completed.


In [130]:
Finance_list = [
    'Financial Analyst', 'Financial Manager', 'Investment Banker', 'Accounting', 'Finance',
    'Accountant', 'Financial Advisor', 'Treasury Analyst', 
    'Credit Analyst', 'Finance Director', 'Portfolio Manager', 'Fico', 'Wealth Advisor',
    'Risk Manager', 'Tax Advisor', 'Controller', 'Auditor', 'Bookkeeper',
    'Corporate Finance Analyst', 'Finance Associate', 'Broker', 'Brokerage', 'Banker', 'Accounts Payable', 'Financial Planning', 'Teller', 'Wealth Mananger'
]

for title in Finance_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Finance'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Finance' and subcategory to 'Unknown'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Finance',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1418070783.py:12: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Financial Analyst
Completed processing for title: Financial Manager
Completed processing for title: Investment Banker
Completed processing for title: Accounting
Completed processing for title: Finance
Completed processing for title: Accountant
Completed processing for title: Financial Advisor
Completed processing for title: Treasury Analyst
Completed processing for title: Credit Analyst
Completed processing for title: Finance Director
Completed processing for title: Portfolio Manager
Completed processing for title: Fico
Completed processing for title: Wealth Advisor
Completed processing for title: Risk Manager
Completed processing for title: Tax Advisor
Completed processing for title: Controller
Completed processing for title: Auditor
Completed processing for title: Bookkeeper
Completed processing for title: Corporate Finance Analyst
Completed processing for title: Finance Associate
Completed processing for title: Broker
Completed processing for title: B

In [131]:
Retail_list = [
    'Retail Sales Associate', 'Retail Manager', 'Store Manager', 'retail', 'Store ', 'stockkeeper',
    'Assistant Store Manager', 'Sales Floor Associate', 'Customer Service Representative', 'Merchandiser',
    'Visual Merchandiser', 'Inventory Manager', 'Retail Buyer', 'Cashier', 
    'Stock Clerk', 'Department Manager', 'Retail Sales Supervisor', 'Merchandising Associate',
    'Loss Prevention Specialist', 'E-commerce Specialist', 'Stock Associate', 'Store Fulfillment', 'Retail Merchandise Processor'
]

for title in Retail_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Retail'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Retail'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Retail',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3081217104.py:12: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Retail Sales Associate
Completed processing for title: Retail Manager
Completed processing for title: Store Manager
Completed processing for title: retail
Completed processing for title: Store 
Completed processing for title: stockkeeper
Completed processing for title: Assistant Store Manager
Completed processing for title: Sales Floor Associate
Completed processing for title: Customer Service Representative
Completed processing for title: Merchandiser
Completed processing for title: Visual Merchandiser
Completed processing for title: Inventory Manager
Completed processing for title: Retail Buyer
Completed processing for title: Cashier
Completed processing for title: Stock Clerk
Completed processing for title: Department Manager
Completed processing for title: Retail Sales Supervisor
Completed processing for title: Merchandising Associate
Completed processing for title: Loss Prevention Specialist
Completed processing for title: E-commerce Specialist
Comp

In [132]:
Food_Industry_list = [
    'Chef', 'Cook', 'Restaurant Manager', 'Sous Chef', 
    'Pastry Chef', 'Food Service Manager', 'Food and Beverage Director', 
    'Barista', 'Baker', 'Line Cook', 'Food Prep Worker', 
    'Dishwasher', 'Catering Manager', 'Food Safety Specialist', 'Nutritionist', 'Claims Service'
]

for title in Food_Industry_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Food Industry'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Food Industry'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Food Industry',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\396859318.py:11: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [145]:
Entertainment_list = [
    'Actor', 'Director', 'Producer', 'Screenwriter', 
    'Cinematographer', 'Film Editor', 'Production Assistant', 
    'Lighting Technician', 'Sound Engineer', 'Costume Designer', 
    'Makeup Artist', 'Talent Agent', 'Event Coordinator', 
    'Music Producer', 'Stage Manager', 'Set Designer', 
    'Script Supervisor', 'Voice Actor', 'Film Critic',
    'Game Designer', 'Game Developer', 'Game Programmer', 
    'Game Artist', 'Game Animator', 'Game Tester', 
    'Level Designer', 'Narrative Designer', 'UX/UI Designer (Gaming)', 
    'Game Producer', 'Sound Designer (Gaming)',
    'Visual Artist', 'Graphic Designer', 'Illustrator', 
    'Art Director', 'Concept Artist', 'Animator', 
    '3D Modeler', 'Storyboard Artist', 'Digital Painter', 
    'Printmaker', 'Art Curator', 'Exhibition Organizer',
    'Composer', 'Musician', 'Music Director', 'Vocal Coach',
    'Sound Technician', 'Music Arranger', 'Music Educator', 
    'Live Sound Engineer', 'Music Therapist', 'Songwriter',
    'Music Supervisor', 'Audio Engineer', 'Music Producer',
    'Author', 'Novelist', 'Copywriter', 'Technical Writer',
    'Content Writer', 'Editorial Writer', 'Blogger', 
    'Creative Writer', 'Ghostwriter', 'Research Writer',
    'Scriptwriter', 'Playwright', 'Editor', 'writer'
]

for title in Entertainment_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Entertainment'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Entertainment'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Entertainment',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3297317519.py:29: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [144]:
Education_list = [
    # Teachers
    'Teacher', 'Classroom Teacher', 'Elementary School Teacher', 'Tutor', 'Trainer',
    'High School Teacher', 'Middle School Teacher', 
    'Special Education Teacher', 'Language Arts Teacher', 'Campus', 'School', 'Dean',
    'Math Teacher', 'Science Teacher', 'History Teacher', 
    'Physical Education Teacher', 'Art Teacher', 'Music Teacher', "Education", 'Educator', 'Coach', 'instructor', 'Pastor', 'preist', 'Church',
    
    # Administrators
    'Principal', 'Vice Principal', 'School Administrator', 
    'School Counselor', 'Dean of Students', 'Registrar', 
    'Director of Curriculum', 'Educational Coordinator', 
    'Educational Consultant',
    
    # Support Staff
    "Teacher's Aide", 'Special Education Aide', 
    'Administrative Assistant', 'School Nurse', 'School Librarian', 
    'Guidance Counselor', 'Educational Therapist',
    
    # Higher Education
    'Professor', 'Associate Professor', 'Assistant Professor', 
    'Lecturer', 'Researcher', 'Dean of Faculty', 
    'Academic Advisor', 'Admissions Counselor', 
    'University Administrator', 'Provost',
    
    # Training and Development
    'Learning and Development Manager'
]

for title in Education_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Education'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Education'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Education',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2934303985.py:33: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [135]:
Police_Security_list = [
    # Police Jobs
    'Police Officer', 'Detective', 'Sergeant', 'Lieutenant', 
    'Captain', 'Chief of Police', 'Criminal Investigator', 
    'Patrol Officer', 'K9 Officer', 'SWAT Team Member', 
    'Traffic Officer', 'School Resource Officer', 
    'Forensic Specialist', 'Crime Scene Investigator', 
    'Police Dispatcher',
    
    # Security Jobs
    'Security Guard', 'Security Officer', 'Loss Prevention Specialist', 
    'Security Manager', 'Security Supervisor', 'Armed Security Officer', 
    'Unarmed Security Officer', 'Event Security', 'Corporate Security', 
    'Private Investigator', 'Security Consultant', 
    'Security Systems Technician', 'CCTV Operator', 
    'Access Control Specialist', 'Risk Assessment Analyst', 'Events Security'
]

for title in Police_Security_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Police and Security'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Police and Security'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Police and Security',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\3687290193.py:22: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [143]:
Legal_list = [
    # Attorneys and Lawyers
    'Attorney', 'Lawyer', 'Criminal Defense Attorney', 
    'Corporate Lawyer', 'Family Lawyer', 'Immigration Lawyer', 
    'Personal Injury Lawyer', 'Real Estate Lawyer', 'Tax Lawyer', 
    'Environmental Lawyer', 'Investigator', 'Legislative', 'Actuary', 'Actual', 'Actuarial',
    
    # Legal Support
    'Paralegal', 'Legal Assistant', 'Legal Secretary', 
    'Legal Researcher', 'Court Clerk', 'Legal Document Specialist', 
    'Legal Transcriptionist',
    
    # Judiciary
    'Judge', 'Magistrate', 'Hearing Officer', 'Court Administrator',
    
    # Compliance and Risk Management
    'Compliance Officer', 'Risk Manager', 'Compliance Analyst', 
    'Regulatory Affairs Specialist',
    
    # Legal Consulting
    'Legal Consultant', 'Contract Manager', 'Legal Advisor', 
    'Mediation Specialist', 'Arbitration Specialist', 'Tax'
]

for title in Legal_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Legal'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Legal'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Legal',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2186690870.py:28: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [142]:
Skilled_trade_list = [
    'Electrician',
    'Plumber',
    'Carpenter',
    'Mason',
    'Roofer', 'Repair',
    'Drywaller', 'Stylist',
    'HVAC Technician',
    'Automotive Mechanic', 'Home Technician', 'Forklift',
    'Diesel Mechanic',
    'Industrial Machinery Mechanic', 'Designer', 
    'Welder',
    'Machinist',
    'CNC Operator',
    'Elevator Installer', 'Installer', 'Pest', 'Roofing', 'Automotive Technician',
    'Boilermaker',
    'Pipefitter',
    'Glassblower', 'Civil Structural Designer',
    'Jeweler', 'Fabricator',
    'Stone Carver', 'Operations', 'Designer',
    'Landscape Architect',
    'Insulation Installer', 'Artisan Fitter',
    'Sign Maker',
    'Mechanic', 'Maintenance', 'Operator', 'Gas Fitter', 'Hairdresser', 'Barber', 'Valve Technician', 'Service Technician'
]

for title in Skilled_trade_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Skilled Trade'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Skilled Trade'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Skilled Trade',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2211412716.py:30: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [141]:
General_management_list = ['Lead', 'recruiter', 'Recruiting', 'Manager', 'Superintendent', 'Team Leader', 'Quality Assurance', 'Quality Control']

for title in General_management_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Management'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Management'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Management',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\1759695325.py:6: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [139]:
Labor_list = [
    'Construction Laborer', 'Laborer', 'Dashers',
    'Demolition Worker',
    'Production Line Worker',
    'Packager',
    'Janitor', 'Custodian',
    'Housekeeper',
    'Cashier',
    'Stock Clerk', 'Cleaner', 'Shipper',
    'Farm Laborer',
    'Landscaping Laborer', 'Production', 'Dispatcher', 
    'Warehouse Worker',
    'Loader', 'Drive', 'dasher', 'Delivery', 
    'Delivery Helper',
    'Attendant', 'warehouse', 'Assembler',
    'Set-Up Crew',
    'Housekeeping', 'Mine', 'Manufacturing', 'Housekeeper', 'Driver', 'Hosts'
]

for title in Labor_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Labor'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Labor'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Labor',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\2205132114.py:23: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [140]:
Service_list = [
    'Customer Service Representative',
    'Call Center Agent',
    'Client Relations Specialist', 'Vehicle Service Agent', 'Customer Experience',
    'Concierge',
    'Travel Agent',
    'Store Manager',
    'Cashier',
    'Waiter', 'Service Coordinator', 'Customer Executive',
    'Field Service', 'hospitality',
    'Personal Trainer',
    'Massage Therapist', 'Customer Relations',
    'Consultant',
    'Financial Advisor', 'Beauty Advisor', 'Client Service', 'Servicing Customer Care',
    'Social Worker',
    'Community Outreach Coordinator',
    'Case Manager', 'Child Protection', 'Server', 'Fan Services', 'Customer Service'
]

for title in Service_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Service'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Service'
                es.update(
                    index='jobs_prd', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Service',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_22864\4153267039.py:23: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [ ]:
#End of Categories--------------------------------------------------------------------------------------------------------

In [189]:
#Beginning of metrics calculation in index 'jobs_health'. Prep

es.indices.delete(index = "jobs_health")

ObjectApiResponse({'acknowledged': True})

In [190]:
#Define mapping of 'jobs_health'

mapping = {
    "mappings": {
        "properties": {
            "category": {
                "type": "keyword"
            },
            "region": {
                "type": "keyword"
            },
            "month": {
                "type": "date",
                "format": "yyyy-MM-dd'T'HH:mm:ss"
            },
            "month_text": {
                "type": "keyword"
            },
            "total_entries": {
                "type": "integer" 
            },
            "average_salary": {
                "type": "float" 
            },
            "timestamp": {
                "type": "date", 
                "format": "yyyy-MM-dd'T'HH:mm:ss.SSSSSS"
            },
            "diff": {
                "type": "float" 
            },
            "diff_percentage": {
                "type": "float" 
            },
            "overall_average_salary": {
                "type": "float" 

            },
            "score" : {
                "type": "float" 

            },
            "status": {
                "type": "keyword" 
            }
        }
    }
}

# Create the index with the defined mapping
es.indices.create(index='jobs_health', body=mapping, ignore=400) 


C:\Users\vicyu\AppData\Local\Temp\ipykernel_13832\2460663055.py:49: DeprecationWarning: Passing transport options in the API method is deprecated. Use 'Elasticsearch.options()' instead.
  es.indices.create(index='jobs_health', body=mapping, ignore=400)


ObjectApiResponse({'acknowledged': True, 'shards_acknowledged': True, 'index': 'jobs_health'})

In [191]:
#Tier1 METRICS SALARY COUNT, AVERAGE, AND OVERALL AVERAGE SALARY

def fetch_and_index_data():
    start = time.time()
    current_time = datetime.now()
    timestamp_str = current_time.isoformat()

    print(timestamp_str)
    print('Start time: ' + str(current_time))

    body = {
        "size": 0,  # No need to return the actual documents
        "aggs": {
            "by_region": {
                "terms": {
                    "field": "region.keyword",
                    "size": 10
                },
                "aggs": {
                    "by_category": {
                        "terms": {
                            "field": "category.keyword",
                            "size": 10
                        },
                        "aggs": {
                            "by_month": {
                                "terms": {
                                    "field": "post_month.keyword",
                                    "size": 12
                                },
                                "aggs": {
                                    "total_entries": {
                                        "value_count": {
                                            "field": "post_month.keyword"
                                        }
                                    },
                                    "average_salary": {
                                        "avg": {
                                            "field": "yearly_salary"
                                        }
                                    }
                                }
                            },
                            # New aggregation for overall average salary
                            "overall_average_salary": {
                                "avg_bucket": {
                                    "buckets_path": "by_month>average_salary"
                                }
                            }
                        }
                    }
                }
            }
        }
    }

    # Execute the search with aggregation
    response = es.search(index='jobs_prd', body=body)
    
    actions = []
    for region_bucket in response['aggregations']['by_region']['buckets']:
        region = region_bucket['key']
        for category_bucket in region_bucket['by_category']['buckets']:
            category = category_bucket['key']
             # Calculate overall average salary across all months
            overall_average_salary = category_bucket['overall_average_salary']['value']
            if overall_average_salary is None:
                overall_average_salary = 0.0
            else:
                overall_average_salary = "{:.2f}".format(overall_average_salary)
            for month_bucket in category_bucket['by_month']['buckets']:
                monthword = month_bucket['key']
                month = datetime.strptime(monthword, "%B %Y").isoformat()
                total_entries = month_bucket['total_entries']['value']
                average_salary = month_bucket['average_salary']['value']
                
                if average_salary is None:
                    average_salary = 0.0
                else:
                    average_salary = "{:.2f}".format(average_salary)
                
            # Calculate overall average salary across all months

            # Prepare document for bulk indexing
                doc = {
                    'region': region,
                    'category': category,
                    'month_text': monthword,
                    'month': month,
                    'total_entries': total_entries,
                    'average_salary': average_salary,
                    'overall_average_salary': overall_average_salary,
                    'timestamp': timestamp_str
                }
            
                actions.append({
                    "_op_type": "index",
                    "_index": "jobs_health",
                    "_source": doc
                })
            
    # Perform bulk indexing
    try:
        if actions:
            bulk(es, actions)
            print(f"Bulk indexed {len(actions)} documents into 'jobs_health'.")
    except Exception as e:
        print(f"An error occurred during bulk indexing: {e}")

    print('Elapsed run time: ' + str(time.time() - start))

if __name__ == "__main__":
    fetch_and_index_data()


2024-09-10T23:13:17.745200
Start time: 2024-09-10 23:13:17.745200
Bulk indexed 135 documents into 'jobs_health'.
Elapsed run time: 0.01919412612915039


In [192]:
#Teir2 - diff 

def update_diff_field():
    """
    Update the 'diff' field in all documents in the 'jobs_health' index.
    The 'diff' field is calculated as 'average_salary' - 'overall_average_salary'.
    """
    # Define the query to fetch all documents that have 'overall_average_salary' and 'average_salary' fields
    query = {
        "query": {
            "bool": {
                "must": [
                    {"exists": {"field": "overall_average_salary"}},
                    {"exists": {"field": "average_salary"}}
                ]
            }
        },
        "_source": ["overall_average_salary", "average_salary"]
    }
    
    # Initialize scroll
    search_result = es.search(index='jobs_health', body=query, scroll='2m', size=1000)
    
    scroll_id = search_result['_scroll_id']
    hits = search_result['hits']['hits']
    
    actions = []
    
    while hits:
        for hit in hits:
            doc_id = hit['_id']
            doc_source = hit['_source']
            
            overall_average_salary = doc_source.get('overall_average_salary')
            average_salary = doc_source.get('average_salary')
            
            if overall_average_salary is not None and average_salary is not None:
                diff = float(average_salary) - float(overall_average_salary)

                update_body = {
                    "doc": {
                        "diff": round(diff, 2)
                    }
                }

                actions.append({
                    "_op_type": "update",
                    "_index": "jobs_health",
                    "_id": doc_id,
                    **update_body
                })

        # Fetch the next batch of results
        search_result = es.scroll(scroll_id=scroll_id, scroll='2m')
        hits = search_result['hits']['hits']
    
    # Perform bulk update
    try:
        if actions:
            bulk(es, actions)
            print(f"Bulk updated {len(actions)} documents in 'jobs_health'.")
        else:
            print("No documents were updated.")
    except Exception as e:
        print(f"An error occurred during bulk update: {e}")

def main():
    start = time.time()

    print('Start time: ' + str(datetime.now()))

    update_diff_field()

    print('Elapsed run time: ' + str(time.time() - start))

if __name__ == "__main__":
    main()


Start time: 2024-09-10 23:13:42.552141
Bulk updated 135 documents in 'jobs_health'.
Elapsed run time: 0.043248891830444336


C:\Users\vicyu\AppData\Local\Temp\ipykernel_13832\595566034.py:22: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  search_result = es.search(index='jobs_health', body=query, scroll='2m', size=1000)


In [193]:
#Teir2 - diff_percentage
def update_diff_percentage_field():
    """
    Update the 'diff_percentage' field in all documents in the 'jobs_health' index.
    The 'diff_percentage' field is calculated as 'diff' / 'overall_average_salary'.
    """
    # Define the query to fetch all documents that have 'diff' and 'overall_average_salary' fields
    query = {
        "query": {
            "bool": {
                "must": [
                    {"exists": {"field": "diff"}},
                    {"exists": {"field": "overall_average_salary"}}
                ]
            }
        },
        "_source": ["diff", "overall_average_salary"]
    }
    
    # Initialize scroll
    search_result = es.search(index='jobs_health', body=query, scroll='2m', size=1000)
    
    scroll_id = search_result['_scroll_id']
    hits = search_result['hits']['hits']
    
    actions = []
    
    while hits:
        for hit in hits:
            doc_id = hit['_id']
            doc_source = hit['_source']
            
            diff = doc_source.get('diff')
            overall_average_salary = float(doc_source.get('overall_average_salary'))
            
            if overall_average_salary and overall_average_salary != 0:
                diff_percentage = diff / overall_average_salary

                update_body = {
                    "doc": {
                        "diff_percentage": round(diff_percentage, 4)
                    }
                }

                actions.append({
                    "_op_type": "update",
                    "_index": "jobs_health",
                    "_id": doc_id,
                    **update_body
                })

        # Fetch the next batch of results
        search_result = es.scroll(scroll_id=scroll_id, scroll='2m')
        hits = search_result['hits']['hits']
    
    # Perform bulk update
    try:
        if actions:
            bulk(es, actions)
            print(f"Bulk updated {len(actions)} documents in 'jobs_health'.")
        else:
            print("No documents were updated.")
    except Exception as e:
        print(f"An error occurred during bulk update: {e}")

def main():
    start = time.time()

    print('Start time: ' + str(datetime.now()))

    update_diff_percentage_field()

    print('Elapsed run time: ' + str(time.time() - start))

if __name__ == "__main__":
    main()


Start time: 2024-09-10 23:13:47.559630
Bulk updated 135 documents in 'jobs_health'.
Elapsed run time: 0.04538416862487793


C:\Users\vicyu\AppData\Local\Temp\ipykernel_13832\1522354933.py:21: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  search_result = es.search(index='jobs_health', body=query, scroll='2m', size=1000)


In [194]:
# Metrics Tier 2- score and status

def update_score_and_status_field():
    """
    Update the 'score' and 'status' fields in all documents in the 'jobs_health' index.
    The 'score' and 'status' fields are calculated based on the 'diff' field.
    """
    # Define the query to fetch all documents that have 'diff' field
    query = {
        "query": {
            "exists": {
                "field": "diff"
            }
        },
        "_source": ["diff"]
    }
    
    # Initialize scroll
    search_result = es.search(index='jobs_health', body=query, scroll='2m', size=1000)
    
    scroll_id = search_result['_scroll_id']
    hits = search_result['hits']['hits']
    
    actions = []
    
    while hits:
        for hit in hits:
            doc_id = hit['_id']
            doc_source = hit['_source']
            
            diff = doc_source.get('diff')
            
            if diff is not None:
                # Calculate score and status
                if diff > 0:
                    score = 1
                    status = "UP"
                elif diff == 0:
                    score = 0
                    status = "UNCHG"
                else:
                    score = -1
                    status = "DOWN"
                
                update_body = {
                    "doc": {
                        "score": score,
                        "status": status
                    }
                }

                actions.append({
                    "_op_type": "update",
                    "_index": "jobs_health",
                    "_id": doc_id,
                    **update_body
                })

        # Fetch the next batch of results
        search_result = es.scroll(scroll_id=scroll_id, scroll='2m')
        hits = search_result['hits']['hits']
    
    # Perform bulk update
    try:
        if actions:
            bulk(es, actions)
            print(f"Bulk updated {len(actions)} documents in 'jobs_health'.")
        else:
            print("No documents were updated.")
    except Exception as e:
        print(f"An error occurred during bulk update: {e}")

def main():
    start = time.time()

    print('Start time: ' + str(datetime.now()))

    update_score_and_status_field()

    print('Elapsed run time: ' + str(time.time() - start))

if __name__ == "__main__":
    main()


Start time: 2024-09-10 23:13:51.129432
Bulk updated 135 documents in 'jobs_health'.
Elapsed run time: 0.043051719665527344


C:\Users\vicyu\AppData\Local\Temp\ipykernel_13832\2646208589.py:19: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  search_result = es.search(index='jobs_health', body=query, scroll='2m', size=1000)


In [195]:
# Metrics Tier 3 - OVERALL SCORE BASED ON WEIGHTS
# Regional weights
regional_weights = {
    "Southeast": 1.1,
    "Northeast": 1.0,
    "Midwest": 0.8,
    "West": 0.7,
    "Southwest": 0.6,
    "Remote": 0.5
}

def calculate_region_scores_for_month(month_text):
    """
    Calculate the average score for each region for a given month_text.
    """
    region_scores = {}
    
    # Fetch average score for each region for the given month_text
    query = {
        "query": {
            "bool": {
                "must": [
                    {"match": {"month_text": month_text}}
                ]
            }
        },
        "aggs": {
            "by_region": {
                "terms": {
                    "field": "region",
                    "size": len(regional_weights)  # Ensure to include all possible regions
                },
                "aggs": {
                    "average_score": {
                        "avg": {
                            "field": "score"
                        }
                    }
                }
            }
        }
    }
    
    response = es.search(index='jobs_health', body=query)
    
    # Process region buckets
    region_buckets = response['aggregations']['by_region']['buckets']
    
    for region_bucket in region_buckets:
        region = region_bucket['key']
        avg_score = region_bucket['average_score']['value']
        print(avg_score, region)
        if avg_score is not None:
            region_scores[region] = avg_score
    
    return region_scores

def calculate_overall_score(region_scores):
    """
    Calculate the overall score based on regional scores and weights.
    """
    weighted_score_sum = 0
    total_weight = 0
    
    for region, score in region_scores.items():
        weight = regional_weights.get(region, 0)
        weighted_score_sum += score * weight
        total_weight += weight
    
    if total_weight > 0:
        overall_score = weighted_score_sum / total_weight
    else:
        overall_score = 0
    
    return overall_score

def insert_overall_score(month_text, overall_score, timestamp):
    """
    Insert a new document into 'jobs_health' with the calculated overall_score.
    """
    doc = {
        "region": "USA",
        "category": "All",
        "month_text": month_text,
        "score": overall_score,
        "timestamp": timestamp
    }
    
    try:
        res = es.index(index='jobs_health', document=doc)
        print(f"Inserted document for month '{month_text}' with score: {overall_score}")
    except Exception as e:
        print(f"An error occurred during document insertion: {e}")

def process_monthly_scores(start_time):
    """
    Process each unique month_text, calculate the regional scores, overall score, and insert the result.
    """
    # Fetch unique month_text values
    query = {
        "aggs": {
            "unique_months": {
                "terms": {
                    "field": "month_text",
                    "size": 1000  # Adjust size if needed
                }
            }
        }
    }
    
    response = es.search(index='jobs_health', body=query)
    #print(response)
    # Process month buckets
    month_buckets = response['aggregations']['unique_months']['buckets']
    #print(month_buckets)
    
    for month_bucket in month_buckets:
        month_text = month_bucket['key']
        print('Month_text:', month_text)
        # Calculate region scores for this month_text
        region_scores = calculate_region_scores_for_month(month_text)
        print('region_scores:', region_scores)
        # Calculate overall score
        overall_score = calculate_overall_score(region_scores)
        print('overall_score:', overall_score)
        # Insert the overall score into the index
        insert_overall_score(month_text, overall_score, start_time)

def main():
    start_time = datetime.utcnow().strftime('%Y-%m-%dT%H:%M:%S.%f')  # Use UTC format and include microseconds
    start = time.time()
    print(f"Start time: {start_time}")
    
    # Process monthly scores
    process_monthly_scores(start_time)
    
    print(f'Elapsed run time: {time.time() - start:.2f} seconds')

if __name__ == "__main__":
    main()



Start time: 2024-09-11T03:13:57.324988
Month_text: April 2024
0.3 Midwest
0.3 Northeast
-0.5 Remote
0.1 Southeast
0.1 Southwest
-0.2 West
region_scores: {'Midwest': 0.3, 'Northeast': 0.3, 'Remote': -0.5, 'Southeast': 0.1, 'Southwest': 0.1, 'West': -0.2}
overall_score: 0.06808510638297874
Inserted document for month 'April 2024' with score: 0.06808510638297874
Month_text: March 2024
-0.4 Midwest
-0.2 Northeast
0.6 Remote
-0.2 Southeast
-0.4 Southwest
0.2 West
region_scores: {'Midwest': -0.4, 'Northeast': -0.2, 'Remote': 0.6, 'Southeast': -0.2, 'Southwest': -0.4, 'West': 0.2}
overall_score: -0.1148936170212766
Inserted document for month 'March 2024' with score: -0.1148936170212766
Month_text: February 2024
-1.0 Northeast
-1.0 Southeast
-1.0 West
-1.0 Remote
region_scores: {'Northeast': -1.0, 'Southeast': -1.0, 'West': -1.0, 'Remote': -1.0}
overall_score: -1.0
Inserted document for month 'February 2024' with score: -1.0
Month_text: January 2024
-1.0 Remote
-1.0 Midwest
-1.0 Northeast
-1.

C:\Users\vicyu\AppData\Local\Temp\ipykernel_13832\1254487210.py:130: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  start_time = datetime.utcnow().strftime('%Y-%m-%dT%H:%M:%S.%f')  # Use UTC format and include microseconds


In [40]:
#creating index for anomalies

# Define index names
source_index = 'jobs_prd'
target_index = 'jobs_anomalies'

def copy_mappings(source_index, target_index):
    # Step 1: Retrieve mappings from the source index
    source_mappings = es.indices.get_mapping(index=source_index)
    
    # Extract the mappings for the source index
    source_mappings = source_mappings[source_index]['mappings']
    
    # Step 2: Create the target index with the same mappings
    # Check if the target index already exists
    if es.indices.exists(index=target_index):
        print(f"Target index '{target_index}' already exists. It will be deleted and recreated.")
        es.indices.delete(index=target_index)

    # Create the target index with the retrieved mappings
    es.indices.create(index=target_index, body={
        'mappings': source_mappings
    })
    
    print(f"Mappings successfully copied from '{source_index}' to '{target_index}'.")

if __name__ == "__main__":
    copy_mappings(source_index, target_index)


Target index 'jobs_anomalies' already exists. It will be deleted and recreated.
Mappings successfully copied from 'jobs_prd' to 'jobs_anomalies'.


In [41]:
#finding and indexing documents into jobs_anomalies

from elasticsearch import Elasticsearch
import numpy as np


source_index = 'jobs_prd'
target_index = 'jobs_anomalies'

def detect_outliers(data):
    """
    Detect outliers using the IQR method.
    """
    if len(data) < 2:
        return None, None
    data = np.array(data, dtype=np.float64)
    q1, q3 = np.percentile(data, [25, 75])
    iqr = q3 - q1
    lower_bound = q1 - 2.7 * iqr
    upper_bound = q3 + 3 * iqr
    return lower_bound, upper_bound

def convert_to_float(value):
    """
    Convert a value to float, handling potential conversion issues.
    """
    try:
        return float(value)
    except (ValueError, TypeError):
        return None

def get_documents_by_pay_period():
    """
    Retrieve all documents grouped by 'pay_period' from the source index.
    """
    pay_periods = {}
    response = es.search(index=source_index, body={
        "query": {
            "match_all": {}
        },
        "size": 10000,  # Adjust size as needed
        "_source": True  # Retrieve all fields
    })

    documents = response['hits']['hits']
    for doc in documents:
        source = doc['_source']
        pay_period = source.get('pay_period')
        if pay_period:
            if pay_period not in pay_periods:
                pay_periods[pay_period] = {'max_salaries': [], 'min_salaries': [], 'med_salaries': [], 'docs': []}
            pay_periods[pay_period]['docs'].append(doc)

            
            max_salary = convert_to_float(source.get('max_salary'))
            min_salary = convert_to_float(source.get('min_salary'))
            med_salary = convert_to_float(source.get('med_salary'))

            if max_salary is not None:
                pay_periods[pay_period]['max_salaries'].append(max_salary)
            if min_salary is not None:
                pay_periods[pay_period]['min_salaries'].append(min_salary)
            if med_salary is not None:
                pay_periods[pay_period]['med_salaries'].append(med_salary)

    return pay_periods

def process_documents():
    pay_periods = get_documents_by_pay_period()

    copied_count = 0
    for pay_period, data in pay_periods.items():
        max_salary_lower, max_salary_upper = detect_outliers(data['max_salaries'])
        min_salary_lower, min_salary_upper = detect_outliers(data['min_salaries'])
        med_salary_lower, med_salary_upper = detect_outliers(data['med_salaries'])

        for doc in data['docs']:
            source = doc['_source']
            max_salary = convert_to_float(source.get('max_salary'))
            min_salary = convert_to_float(source.get('min_salary'))
            med_salary = convert_to_float(source.get('med_salary'))

            is_outlier = False
            if max_salary_lower is not None and max_salary_upper is not None:
                if max_salary is not None and (max_salary < max_salary_lower or max_salary > max_salary_upper):
                    is_outlier = True
            if min_salary_lower is not None and min_salary_upper is not None:
                if min_salary is not None and (min_salary < min_salary_lower or min_salary > min_salary_upper):
                    is_outlier = True
            if med_salary_lower is not None and med_salary_upper is not None:
                if med_salary is not None and (med_salary < med_salary_lower or med_salary > med_salary_upper):
                    is_outlier = True

            if is_outlier:
                # Index outlier document into the target index
                es.index(index=target_index, id=doc['_id'], document=source)
                copied_count += 1

    print(f"Processing complete. {copied_count} outlier documents copied to '{target_index}'.")

if __name__ == "__main__":
    process_documents()


Processing complete. 47 outlier documents copied to 'jobs_anomalies'.


In [ ]:
#creating new elasticsearch index called 'jobs_prd_filtered' and indexing documents from csv file

import csv
import requests

url = 'http://localhost:9200/'  

def index_document(document):
    response = requests.post(url + 'jobs_prd_filtered/_doc/', json=document, auth=("username", "password"))
    if response.status_code == 201:
        print("Document indexed successfully.")
    else:
        print("Failed to index document.")
        print("Response:", response.text)

with open("jobs_prd.csv", "r", encoding="utf-8") as f1:
    print("YOUR DATA IS PROCESSING. DO NOT RERUN THE CODE")
    reader = csv.reader(f1)
    
    headers = next(reader)  # Skip header row
    
    for line in reader:
        if line and len(line) >= 28:
            jobs_prd = {
                'job_id': line[0],
                'company_name': line[1],
                'title': line[2],
                'description': line[3],
                'max_salary': line[4],
                'pay_period': line[5],
                'location': line[6],
                'company_id': line[7],
                'views': line[8],
                'med_salary': line[9],
                'min_salary': line[10],
                'formatted_work_type': line[11],
                'applies': line[12],
                'remote_allowed': line[14],
                'job_posting_url': line[15],
                'application_url': line[16],
                'application_type': line[17],
                'formatted_experience_level': line[20],
                'skills_desc': line[21],
                'posting_domain': line[23],
                'sponsored': line[24],
                'work_type': line[25],
                'currency': line[26],
                'compensation_type': line[27],
                'post_date': line[31],
                'expiration_date': line[32],
                'post_month': line[33]
            }
            index_document(jobs_prd)


YOUR DATA IS PROCESSING. DO NOT RERUN THE CODE
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed successfully.
Document indexed succes

In [9]:
#removing outliers from jobs_prd_filtered

from elasticsearch import Elasticsearch, helpers

def get_anomalous_job_ids(index_name):
    """Retrieve all job_id values from the specified index."""
    job_ids = set()
    scroll = '2m'  # Scroll timeout
    search = {
        '_source': ['job_id'],  # Only retrieve the job_id field
        'query': {
            'match_all': {}  # Match all documents to get all job_ids
        }
    }
    
    # Initialize the scroll
    response = es.search(index=index_name, body=search, scroll=scroll, size=1000)
    scroll_id = response['_scroll_id']
    hits = response['hits']['hits']
    
    while hits:
        for hit in hits:
            job_ids.add(hit['_source']['job_id'])
        
        # Fetch the next batch of results
        response = es.scroll(scroll_id=scroll_id, scroll=scroll)
        scroll_id = response['_scroll_id']
        hits = response['hits']['hits']
    
    # Clear scroll context
    es.clear_scroll(scroll_id=scroll_id)
    
    return job_ids

def delete_documents(index_name, job_ids):
    """Delete documents from the index where job_id exists in the given set."""
    if not job_ids:
        print("No job_ids to delete.")
        return
    
    # Create a delete-by-query request
    query = {
        "query": {
            "terms": {
                "job_id": list(job_ids)
            }
        }
    }
    
    # Execute the delete-by-query request
    response = es.delete_by_query(index=index_name, body=query)
    
    print("Deleted documents:", response['deleted'])

def main():
    # Retrieve job_ids from the anomalies index
    anomalies_index = 'jobs_anomalies'
    job_ids = get_anomalous_job_ids(anomalies_index)
    
    # Delete documents from the filtered index
    filtered_index = 'jobs_prd_filtered'
    delete_documents(filtered_index, job_ids)

if __name__ == "__main__":
    main()


Deleted documents: 47


C:\Users\vicyu\AppData\Local\Temp\ipykernel_1016\1958228620.py:15: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  response = es.search(index=index_name, body=search, scroll=scroll, size=1000)


In [27]:
#CLEANING FILTERED INDEX-------------------------------------------------------------------------------------------------------------------------------------------------------------

In [28]:
#calculate annual salary for all entries where 'salary' exists
#painless scripting

script = {
    "script": {
        "source": """
            // Initialize minSalary
            def minSalary = null;

            // Check if min_salary is a String and convert it if not empty
            if (ctx._source.min_salary instanceof String) {
                if (ctx._source.min_salary.length() > 0) {
                    try {
                        minSalary = Double.parseDouble(ctx._source.min_salary);
                    } catch (NumberFormatException e) {
                        // Handle cases where the string cannot be parsed
                        minSalary = null; // Set to null if parsing fails
                    }
                } else {
                    minSalary = null; // Set to null if the string is empty
                }
            } else if (ctx._source.min_salary instanceof Number) {
                minSalary = ((Number) ctx._source.min_salary).doubleValue();
            } else {
                return; // Exit if min_salary is neither a String nor a Number
            }

            // Calculate yearly_salary based on pay_period
            if (minSalary == null) {
                ctx._source.yearly_salary = null;
            } else if (ctx._source.pay_period == 'YEARLY') {
                ctx._source.yearly_salary = minSalary;
            } else if (ctx._source.pay_period == 'MONTHLY') {
                ctx._source.yearly_salary = minSalary * 12;
            } else {
                ctx._source.yearly_salary = minSalary * 1760;
            }
        """,
        "lang": "painless"
    },
    "query": {
        "match_all": {}  # Adjust this query to select specific documents if needed
    },
    "conflicts": "proceed"  # Allow the update to proceed even if there are version conflicts
}

# Execute the update_by_query request
try:
    response = es.update_by_query(index="jobs_prd_filtered", body=script)
    print("Update by Query Response:", response)
except exceptions.RequestError as e:
    print(f"RequestError: {e.info}")
except exceptions.ConnectionError as e:
    print(f"ConnectionError: {e}")
except Exception as e:
    print(f"An error occurred: {e}")

Update by Query Response: {'took': 23222, 'timed_out': False, 'total': 123802, 'updated': 123802, 'deleted': 0, 'batches': 124, 'version_conflicts': 0, 'noops': 0, 'retries': {'bulk': 0, 'search': 0}, 'throttled_millis': 0, 'requests_per_second': -1.0, 'throttled_until_millis': 0, 'failures': []}


In [30]:
#DATA PARSING---------------------------------------------------------------------------------------------------------

#make new feild 'state'
#fill 'state' with last two letters of 'location'
#painless scripting

index_name = 'jobs_prd_filtered'

# Define the update script
script = {
    "source": """
        if (ctx._source.containsKey('location') && ctx._source['location'] != null) {
            String location = ctx._source['location'];
            if (location.length() >= 2) {
                String stateAbbreviation = location.substring(location.length() - 2).toUpperCase();
                ctx._source.state = stateAbbreviation;
            } else {
                ctx._source.state = "Unknown";
            }
        }
    """,
    "lang": "painless"
}

# Search for documents that need to be updated
search_query = {
    "query": {
        "exists": {
            "field": "location"  # Adjust if the field name is different
        }
    }
}

# Scroll to retrieve all documents
scroll_size = 1000
scroll = '2m'
response = es.search(index=index_name, body=search_query, scroll=scroll, size=scroll_size)
scroll_id = response['_scroll_id']

# Process each batch of documentspostings
while True:
    bulk_updates = []
    for hit in response['hits']['hits']:
        doc_id = hit['_id']
        bulk_updates.append({
            "_op_type": "update",
            "_index": index_name,
            "_id": doc_id,
            "script": script
        })
    
    # Perform the bulk update
    if bulk_updates:
        helpers.bulk(es, bulk_updates)
    
    # Fetch the next batch
    response = es.scroll(scroll_id=scroll_id, scroll=scroll)
    scroll_id = response['_scroll_id']
    
    # Break the loop if no more documents
    if not response['hits']['hits']:
        break

# Clear the scroll context
es.clear_scroll(scroll_id=scroll_id)

print("Update completed.")

C:\Users\vicyu\AppData\Local\Temp\ipykernel_1016\3927256866.py:37: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  response = es.search(index=index_name, body=search_query, scroll=scroll, size=scroll_size)


Update completed.


In [104]:
NY_list = ['New York City', 'New York City Metropolitan Area', 
"New York City Metropolitan Area", 'New York, United States', '*NY', 'Albany, New York Metropolitan Area', 'New York, New York, United States', 'Brooklyn, New York, United States']

for i in NY_list:
    result = es.search(index='jobs_prd_filtered' , body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'NY'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("I'm walkin' here") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\4079737888.py:5: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered' , body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


I'm walkin' here
I'm walkin' here
I'm walkin' here
I'm walkin' here
I'm walkin' here
I'm walkin' here
I'm walkin' here
I'm walkin' here


In [105]:
CA_list = ['California, United States', 'San Francisco Bay Area', 'Los Angeles Metropolitan Area', 'Los Angeles, California, United States', 'San Diego Metropolitan Area', 'Greater Sacramento']

for i in CA_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'CA'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print('success') 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3074254905.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success
success
success


In [106]:
TX_list = ['Texas, United States', 'Dallas-Fort Worth Metroplex', 'Greater Houston', 'Austin, Texas Metropolitan Area', 'San Antonio, Texas Metropolitan Area', 'TX']

for i in TX_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'TX'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3716044939.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success
success
success


In [107]:
DC_list = ['Washington DC-Baltimore Area', 'Washington District of Columbia', 'Washington DC, United States', 'District of Columbia, United States']

for i in DC_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'DC'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success
success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\611429681.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [108]:
FL_list = ['Florida, United States', 'Tampa Metropolitan Area', 'Orlando Metropolitan Area', 'Greater Orlando', "Miami-Fort Lauderdale Area", 'Greater Tampa Bay Area', 'Gainesville Metropolitan Area']

for i in FL_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'FL'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3290421172.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success
success
success
success


In [109]:
GA_list = ['Atlanta Metropolitan Area', 'Georgia, United States']

for i in GA_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'GA'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1053847243.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [110]:
NJ_list = ['New Jersey, United States']

for i in NJ_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'NJ'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3213911716.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success


In [111]:
NC_list = ['North Carolina, United States', 'Raleigh-Durham-Chapel Hill Area', 'Charlotte Metro']

for i in NC_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'NC'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3676839724.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success
success


In [112]:
IL_list = ['Illinois, United States', 'Greater Chicago Area']

for i in IL_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'IL'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\2958172069.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [113]:
KY_list = ['Kentucky, United States', 'Nashville Metropolitan Area']

for i in KY_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'KY'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1935595042.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [114]:
PA_list = ['Pennsylvania, United States', 'Pilidalphia Metropolitan Area']

for i in PA_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'PA'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3338727425.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [115]:
OH_list = ['Ohio, United States', 'Columbus, Ohio Metropolitan Area', 'Cincinnati Metropolitan Area']

for i in OH_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'OH'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\2890568707.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [116]:
MA_list = ['Massachusetts, United States', 'Greater Boston']

for i in MA_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'MA'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\2719202487.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [117]:
CO_list = ['Colorado, United States', 'Denver Metropolitan Area', 'Aurora, Colorado, United States']

for i in CO_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'CO'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1682199721.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [118]:
VA_list = ['Virginia, United States', 'VA']

for i in VA_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'VA'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1489325771.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


success
success


In [119]:
AZ_list = ['Greater Phoenix Area', "Arizona, United States"]

for i in AZ_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'AZ'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\198326360.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [120]:
MN_list = ['Greater Minneapolis-St. Paul Area', "Minnesota, United States"]

for i in MN_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'MN'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3336824094.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [121]:
WI_list = [ "Wisconsin, United States"]

for i in WI_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'WI'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\910193969.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [122]:
MO_list = [ "Missouri, United States", 'St Louis, Missouri, United States', 'Greater St. Louis', 'Greater Jefferson City Area', 'Greater Columbia, Missouri Area']

for i in MO_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'MO'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success
success
success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3464618525.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [123]:
IN_list = ['Indiana, United States', 'Greater Indianapolis', 'Indianapolis Metropolitan Area']

for i in IN_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'IN'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1875484719.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [124]:
MT_list = ['Montana, United States']

for i in MT_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'MT'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1353568207.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [125]:
NV_list = ['Nevada, United States', 'Las Vegas Metropolitan Area']

for i in NV_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'NV'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("Let's go gambing!") 

Let's go gambing!
Let's go gambing!


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3645285520.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [126]:
KS_list = ['Kansas, United States', 'Kansas City Metropolitan Area', 'Witchita Metropolitan Area', 'Wichita, Kansas Metropolitan Area']

for i in KS_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'KS'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success
success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\4254123761.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [127]:
MI_list = ['Michigan, United States', 'Detroit Metropolitan Area', 'Ann Aarbor Area', 'Lansing Metropolitan Area']

for i in MI_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'MI'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success
success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\698289481.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [128]:
OR_list = ['Oregan, United States', 'Portland, Oregon Metropolitan Area', 'Portland Metropolitan Area', 'Oregon, United States']

for i in OR_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'OR'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success
success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1983644109.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [129]:
WA_list = ['Washington, United States', 'Washington State, United States', 'Greater Seattle Area', 'Seattle Metropolitan Area', 'Seattle, Washington, United States']

for i in WA_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'WA'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success
success
success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\516163002.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [130]:
UT_list = ['Utah, United States', 'Salt Lake City Metropolitan Area']

for i in UT_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'UT'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\2264391005.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [131]:
MD_list = ['Maryland, United States', 'Baltimore Metropolitan Area', 'Greater Baltimore Metropolitan Area', 'Annapolis Metropolitan Area', 'Annapolis, Maryland, United States']

for i in MD_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'MD'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success
success
success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3894502989.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [132]:
AR_list = ['Arkansas, United States', 'Little Rock Metropolitan Area']

for i in AR_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'AR'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success
success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3961360917.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [133]:
SC_list = ['South Carolina, United States']

for i in SC_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'SC'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3841643901.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [134]:
TN_list = ['Tennessee, United States']

for i in TN_list:
    result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        #print(f"Document ID: {document_id}")
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'TN'}})
        #print(es.search(index='jobs_prd', body={'query': {'match': {'location': i}}}))
    print("success") 

success


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\352264929.py:4: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': {'match_phrase': {'location': i}}}, scroll='2m', size=10000)


In [103]:

# Making all documents with location "United States" have state "Unknown"
result = es.search(index= 'jobs_prd_filtered' , body={'query': {'match_phrase': {'location': 'United States'}}}, scroll='2m', size=10000)
hits = result['hits']['hits']

for hit in hits:
    document_id = hit['_id']          # Access the '_id' field
    #print(f"Document ID: {document_id}")
    es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'state': 'Remote'}})
    es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'region': 'Remote'}})

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\943128683.py:2: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index= 'jobs_prd_filtered' , body={'query': {'match_phrase': {'location': 'United States'}}}, scroll='2m', size=10000)


KeyboardInterrupt: 

In [135]:
#Giving documents in jobs_prd_filtered a region

In [136]:
SE_list= ["AR", "LA", "MS", "AL", "TN", "KY", "WV", "FL", "GA", "SC", "NC", "VA", "DC"]
for i in SE_list:
    result = es.search(index='jobs_prd_filtered', body={'query': { 'bool': { 'must': [ {'match': {'state': i}}]}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'region': 'Southeast'}})
        #print(es.search(index='jobs_test2', body={'query': {'match': {'state': i}}}))
print('Dixies') 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1864319291.py:3: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': { 'bool': { 'must': [ {'match': {'state': i}}]}}}, scroll='2m', size=10000)


Dixies


In [137]:
SW_list= ["AZ", "NM", "TX", "OK"]
for i in SW_list:
    result = es.search(index='jobs_prd_filtered', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'region': 'Southwest'}})
        #print(es.search(index='jobs_test2', body={'query': {'match': {'state': i}}}))
print('Yeehaw') 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3737068648.py:3: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)


Yeehaw


In [138]:
W_list= ["WA", "OR", "ID", "MT", "WY", "CO", "UT", "NV", "CA", "HI", "AK"]
for i in W_list:
    result = es.search(index='jobs_prd_filtered', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'region': 'West'}})
        #print(es.search(index='jobs_test2', body={'query': {'match': {'state': i}}}))
print('Liberals') 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\839776143.py:3: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)


Liberals


In [139]:
NE_list= ["ME", "VT", "NH", "MA", "CT", "RI", "NY", "PA", "NJ", "DE", "MD"]
for i in NE_list:
    result = es.search(index='jobs_prd_filtered', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'region': 'Northeast'}})
        #print(es.search(index='jobs_test2', body={'query': {'match': {'state': i}}}))
print('Woke') 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3227946798.py:3: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)


Woke


In [140]:
MW_list= ["ND", "SD", "NE", "KS", "MN", "IA", "MO", "WI", "IL", "IN", "MI", "OH"]
for i in MW_list:
    result = es.search(index='jobs_prd_filtered', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)
    hits = result['hits']['hits']

    for hit in hits:
        document_id = hit['_id']          # Access the '_id' field
        es.update(index='jobs_prd_filtered', id= document_id, body={'doc': {'region': 'Midwest'}})
        #print(es.search(index='jobs_test2', body={'query': {'match': {'state': i}}}))
print('Who?') 

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1300607036.py:3: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(index='jobs_prd_filtered', body={'query': { 'bool': { 'must': [ {'match': {'state': i}} ]}}}, scroll='2m', size=10000)


Who?


In [ ]:
#CATEGORIES FOR FILTERED

In [141]:
#Painless scripting
index_name = 'jobs_prd_filtered'


update_body = {
    "script": {
        "source": "ctx._source.subcategory = 'Unknown'",
        "lang": "painless"
    },
    "query": {
        "match_all": {}
    }
}

try:
    response = es.update_by_query(index=index_name, body=update_body)
    print("Update by query response:", response)
except NotFoundError:
    print(f"Index {index_name} not found")
except Exception as e:
    print("An error occurred:", str(e))

Update by query response: {'took': 25920, 'timed_out': False, 'total': 123802, 'updated': 123802, 'deleted': 0, 'batches': 124, 'version_conflicts': 0, 'noops': 0, 'retries': {'bulk': 0, 'search': 0}, 'throttled_millis': 0, 'requests_per_second': -1.0, 'throttled_until_millis': 0, 'failures': []}


In [143]:
#UPDATES ALL ENTRIES TO HAVE CATEGORY : 'UNKNOWN'
#DOES NOT WORK AS INTENDED
exists_list = [
    'Service', 'Labor', 'General Management', 'Skilled Trade', 'IT', 
    'Scientific Development', 'Food Industry', 'Uncategorized Health', 
    'Marketing', 'Software', 'Sales', 'Medical', 'Retail', 'Finance', 
    'Entertainment', 'Education', 'Legal', 'Admin', 'Scientific Research', 
    'Data', 'Health Ally', 'Healthcare Management', 'Mental Health', 
    'Police and Security', 'Public Health'
]

# Convert the list to a set for faster lookup
exists_set = set(exists_list)

def update_documents_not_in_list():
    try:
        # Query to find documents where 'category' is not in the exists_list
        query = {
            "query": {
                "bool": {
                    "must_not": {
                        "terms": {
                            "category": list(exists_set)
                        }
                    }
                }
            }
        }

        # Perform the search with scroll
        result = es.search(
            index='jobs_prd_filtered',
            body=query,
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )
        
        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']
        
        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Unknown'
                es.update(index='jobs_prd_filtered', id=document_id, body={'doc': {'category': 'Unknown'}})
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)
        
        print("Completed processing all documents not in the list.")

    except Exception as e:
        print(f"An error occurred: {e}")

# Run the update function
update_documents_not_in_list()


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\2711295639.py:31: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing all documents not in the list.


In [144]:
IT_list = ['IT ', 'Solutions Architect', 'System Architect', 'Artifical Intelligence', 'Programming', 'Full-stack', 'Back End Developer', 'Systems Admin', 'Cyber Security', 'Cybersecurity', 'Network', 'Systems Engineer', 'Chief Information Officer', ' CIO', 'Help Desk', 'Technical Support', 'Innovation Specialist', 'IoT ', 'Programmer']

for title in IT_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        #"must_not": {
                            #"match_phrase": {'category': 'IT'}
                        #}
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']

                # Update the document to set the category to 'IT'
                es.update(index='jobs_prd_filtered', id=document_id, body={'doc': {'category': 'IT'}, 'doc': {'subcategory': 'Unknown'}})
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        print(f"Completed processing for title: {title}")

        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)
    
    except Exception as e:
        print(f"An error occurred for title {title}: {e}")

print("All searches and updates completed.")

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\957216481.py:6: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: IT 
Completed processing for title: Solutions Architect
Completed processing for title: System Architect
Completed processing for title: Artifical Intelligence
Completed processing for title: Programming
Completed processing for title: Full-stack
Completed processing for title: Back End Developer
Completed processing for title: Systems Admin
Completed processing for title: Cyber Security
Completed processing for title: Cybersecurity
Completed processing for title: Network
Completed processing for title: Systems Engineer
Completed processing for title: Chief Information Officer
Completed processing for title:  CIO
Completed processing for title: Help Desk
Completed processing for title: Technical Support
Completed processing for title: Innovation Specialist
Completed processing for title: IoT 
Completed processing for title: Programmer
All searches and updates completed.


In [145]:

Software_list = ['Software', '.NET Developer', 'Software Development', 'Java', 'C++']

for title in Software_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Software'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']  # Access the '_id' field

                # Update the document to set the category to 'IT' and subcategory to 'Software'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'IT',
                            'subcategory': 'Software'
                        }
                    }
                )

            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id,
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)
        
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title {title}: {e}")

print('All searches and updates completed.')


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\981340781.py:6: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Software
Completed processing for title: .NET Developer
Completed processing for title: Software Development
Completed processing for title: Java
Completed processing for title: C++
All searches and updates completed.


In [146]:

Data_list = ['Data', 'Database', 'Mongo DB']

for title in Data_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Data'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'IT' and subcategory to 'Data'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'IT',
                            'subcategory': 'Data'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)
        
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title {title}: {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3476326542.py:6: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Data
Completed processing for title: Database
Completed processing for title: Mongo DB
All searches and updates completed.


In [172]:

Admin_list = [
    'Administrative Assistant', 'Right-of-Way Agent', 'Associate Facilitator', 'secretary', 'Contract Coordinator', 'People Development',
    'Office Manager', 'Executive Assistant', 'Receptionist', 'Data Entry Clerk', 'Office Clerk', 'HR',
    'Administrative Coordinator', 'Planner', 'Office Administrator', 'Personal Assistant', 'Program Coordinator', 'Administrative Clerk',
    'Executive Secretary', 'Office Support Specialist', 'File Clerk', 'Human Resources', 'Human Resources Assistant', 'Outpatient Coordinator',
    'Payroll Clerk', 'Administrative Manager', 'Project Administrator', 'Accounts Receivable', 'Legal Secretary',
    'Facilities Coordinator', 'Eligibility Supervisor', 'Scheduler', 'Records Manager', 'Travel Coordinator', 'Front Desk',
    'Licensing Coordinator', 'Claims Examiner', 'Operations Coordinator', 'Purchasing Coordinator'
]

for title in Admin_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Admin'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Admin' and subcategory to 'Unknown'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Admin',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)
        
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title {title}: {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\205572094.py:14: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Administrative Assistant
Completed processing for title: Right-of-Way Agent
Completed processing for title: Associate Facilitator
Completed processing for title: secretary
Completed processing for title: Contract Coordinator
Completed processing for title: People Development
Completed processing for title: Office Manager
Completed processing for title: Executive Assistant
Completed processing for title: Receptionist
Completed processing for title: Data Entry Clerk
Completed processing for title: Office Clerk
Completed processing for title: HR
Completed processing for title: Administrative Coordinator
Completed processing for title: Planner
Completed processing for title: Office Administrator
Completed processing for title: Personal Assistant
Completed processing for title: Program Coordinator
Completed processing for title: Administrative Clerk
Completed processing for title: Executive Secretary
Completed processing for title: Office Support Specialist
C

In [148]:
Medical_list = [
    'Doctor', 'Nurse', 'Pharmacy', 'Veterinarian', 'Urology', 'Endodontist', 'Neuroscience', 'Surg', 'Vet', 
    'Medication Aide', 'X-Ray', 'Anesthesiology', 'Orthopedic', 'RN', 'Radiology', 'Home Health', 'Pharmacist', 
    'Physician', 'Dentist', 'Hygienist', 'Dosimetrist', 'Neurology', 'Audiologist', 'Oncology', 'Radiation Therapist',
    'Medical', 'Surgeon', 'Medicine Technologist', 'Anesthesiologist', 'Dental', 'Surgical', 'Neurological', 
    'Nursing', 'MRI', 'Veterinary', 'CMC', 'Radiologist', 'Medical Laboratory Technician', 'Paramedic', 'Patient Care', 
    'Phlebotomist', 'IR Tech', 'PM&R', 'Paraprofessional', 'Physical Therapy'
]

for title in Medical_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Medical'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Healthcare' and subcategory to 'Medical'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Healthcare',
                            'subcategory': 'Medical'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1307997044.py:13: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Doctor
Completed processing for title: Nurse
Completed processing for title: Pharmacy
Completed processing for title: Veterinarian
Completed processing for title: Urology
Completed processing for title: Endodontist
Completed processing for title: Neuroscience
Completed processing for title: Surg
Completed processing for title: Vet
Completed processing for title: Medication Aide
Completed processing for title: X-Ray
Completed processing for title: Anesthesiology
Completed processing for title: Orthopedic
Completed processing for title: RN
Completed processing for title: Radiology
Completed processing for title: Home Health
Completed processing for title: Pharmacist
Completed processing for title: Physician
Completed processing for title: Dentist
Completed processing for title: Hygienist
Completed processing for title: Dosimetrist
Completed processing for title: Neurology
Completed processing for title: Audiologist
Completed processing for title: Oncology


In [173]:

Healthcare_Management_list = [
    'Healthcare Administrator', 'Medical Office Manager', 'Management training', 'Head of Quality', 'VP', 'CFO', 'VP/CFO',
    'Clinical Manager', 'Health Services Manager', 'Practice Manager', 'Patient',
    'Medical Director', 'Health Information Manager', 'Hospital Administrator', 'Patient Service Representative', 'Credentialing Coordinator',
]

for title in Healthcare_Management_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Healthcare Management'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Healthcare' and subcategory to 'Healthcare Management'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Healthcare',
                            'subcategory': 'Healthcare Management'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


Completed processing for title: Healthcare Administrator
Completed processing for title: Medical Office Manager
Completed processing for title: Management training
Completed processing for title: Head of Quality


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\885919767.py:10: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: VP
Completed processing for title: CFO
Completed processing for title: VP/CFO
Completed processing for title: Clinical Manager
Completed processing for title: Health Services Manager
Completed processing for title: Practice Manager
Completed processing for title: Patient
Completed processing for title: Medical Director
Completed processing for title: Health Information Manager
Completed processing for title: Hospital Administrator
Completed processing for title: Patient Service Representative
Completed processing for title: Credentialing Coordinator
All searches and updates completed.


In [150]:

Allied_Health_list = [
    'Physical Therapist', 'Occupational Therapist', 
    'Speech-Language Pathologist', 'Dietitian/Nutritionist', 
    'Respiratory Therapist', 'Health Educator', 
    'Certified Nursing Assistant (CNA)', 'Clinical Associate'
]

for title in Allied_Health_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Health Ally'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Healthcare' and subcategory to 'Health Ally'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Healthcare',
                            'subcategory': 'Health Ally'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\3104664220.py:11: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Physical Therapist
Completed processing for title: Occupational Therapist
Completed processing for title: Speech-Language Pathologist
Completed processing for title: Dietitian/Nutritionist
Completed processing for title: Respiratory Therapist
Completed processing for title: Health Educator
Completed processing for title: Certified Nursing Assistant (CNA)
Completed processing for title: Clinical Associate
All searches and updates completed.


In [151]:
Public_Health_list = [
    'Epidemiologist', 'Public Health Analyst', 'Biostatistician', 
    'Health Research Scientist', 'Community Health Worker', 
    'Health Policy Analyst'
]

for title in Public_Health_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Public Health'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Healthcare' and subcategory to 'Public Health'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Healthcare',
                            'subcategory': 'Public Health'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1757769010.py:10: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Epidemiologist
Completed processing for title: Public Health Analyst
Completed processing for title: Biostatistician
Completed processing for title: Health Research Scientist
Completed processing for title: Community Health Worker
Completed processing for title: Health Policy Analyst
All searches and updates completed.


In [152]:
Mental_Health_list = [
    'Psychologist', 'Counselor', 'Clinical Social Worker', 'Family Therapist',
    'Psychiatrist', 'Substance Abuse Counselor', 
    'Marriage and Family Therapist', 'Mental Health', 'PSYCHOLOGICAL'
]


for title in Mental_Health_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Mental Health'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Healthcare' and subcategory to 'Mental Health'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Healthcare',
                            'subcategory': 'Mental Health'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1594767157.py:11: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Psychologist
Completed processing for title: Counselor
Completed processing for title: Clinical Social Worker
Completed processing for title: Family Therapist
Completed processing for title: Psychiatrist
Completed processing for title: Substance Abuse Counselor
Completed processing for title: Marriage and Family Therapist
Completed processing for title: Mental Health
Completed processing for title: PSYCHOLOGICAL
All searches and updates completed.


In [153]:
Uncategorized_Health_list = [
    'Health', 
    'Healthcare', 
    'Medical'
]

for title in Uncategorized_Health_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Healthcare'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                print(document_id)
                # Update the document to set the category to 'Healthcare' and subcategory to 'Unknown'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Healthcare',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\2352069307.py:10: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


oO8i7JEBhh_QmFfD4ujZ
UPAn7JEBhh_QmFfDZ2Nc
Mu8f7JEBhh_QmFfDeoug
iO8i7JEBhh_QmFfDvOSO
cu8b7JEBhh_QmFfD2yp7
HPAm7JEBhh_QmFfDAD2w
8e8h7JEBhh_QmFfDbsDH
_PAk7JEBhh_QmFfDzhuC
Ju8e7JEBhh_QmFfDZm0p
3_An7JEBhh_QmFfDdWRl
6fAm7JEBhh_QmFfDxVEc
lPAj7JEBhh_QmFfD0wGY
u-4a7JEBhh_QmFfDGfpn
hu8c7JEBhh_QmFfDEy9-
Eu8i7JEBhh_QmFfDk-CQ
Ee8j7JEBhh_QmFfDu__i
4e4X7JEBhh_QmFfD675k
ou4X7JEBhh_QmFfD3r0N
ve4X7JEBhh_QmFfD6b7L
s-8e7JEBhh_QmFfDPGi2
9-8f7JEBhh_QmFfD1pQ3
fe8e7JEBhh_QmFfD4Xoh
2-8e7JEBhh_QmFfDNGde
nPAk7JEBhh_QmFfDcBLO
vO8i7JEBhh_QmFfDBtDR
8_Ak7JEBhh_QmFfDcxLg
9e8i7JEBhh_QmFfDGtLm
Xe8e7JEBhh_QmFfDem89
-_An7JEBhh_QmFfDG1po
YPAn7JEBhh_QmFfDHlvz
I-8c7JEBhh_QmFfD1UMp
4O8e7JEBhh_QmFfDNGeL
De8d7JEBhh_QmFfDP06-
C-8a7JEBhh_QmFfDqQqV
7-4W7JEBhh_QmFfDy6Gy
1e8c7JEBhh_QmFfDCy6w
8fAl7JEBhh_QmFfDaiyd
xu8j7JEBhh_QmFfDN_G7
zO8g7JEBhh_QmFfD7bLu
y-4Y7JEBhh_QmFfDW8pN
x-8c7JEBhh_QmFfDizsD
ZO4Z7JEBhh_QmFfDZ-c-
TO8g7JEBhh_QmFfDLp4P
kO8f7JEBhh_QmFfD7ZeX
afAn7JEBhh_QmFfDX2Ii
cO8b7JEBhh_QmFfD0ik0
2e8d7JEBhh_QmFfDo1gh
9PAl7JEBhh_Qm

In [174]:
Sales_list = [
    'Sales Representative', 'Sales Manager', 'Account Manager', 'Sales Associate', 
    'Business Development Manager', 'Sales Director', 'Selling', 
    'Regional Sales Manager', 'Inside Sales Representative', 
    'Field Sales Representative', 'Sales Engineer', 'Sales Development Representative', 'Sales', 
    'Salesperson', 'Select Account Executive', 'Account Executive'
]

for title in Sales_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Sales'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Sales' and subcategory to 'Unknown'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Sales',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\4060517893.py:12: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Sales Representative
Completed processing for title: Sales Manager
Completed processing for title: Account Manager
Completed processing for title: Sales Associate
Completed processing for title: Business Development Manager
Completed processing for title: Sales Director
Completed processing for title: Selling
Completed processing for title: Regional Sales Manager
Completed processing for title: Inside Sales Representative
Completed processing for title: Field Sales Representative
Completed processing for title: Sales Engineer
Completed processing for title: Sales Development Representative
Completed processing for title: Sales
Completed processing for title: Salesperson
Completed processing for title: Select Account Executive
Completed processing for title: Account Executive
All searches and updates completed.


In [175]:
Marketing_list = [
    'Marketing Manager', 'Marketing Director', 'Marketing Coordinator', 
    'Marketing Specialist', 'Content Marketing Manager', 
    'Digital Marketing Specialist', 'SEO Specialist', 'Social Media Manager', 
    'Brand Manager', 'Product Marketing Manager', 'Marketing', 'Search Planner'
]

for title in Marketing_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Marketing'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Marketing' and subcategory to 'Unknown'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Marketing',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\4032579599.py:11: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Marketing Manager
Completed processing for title: Marketing Director
Completed processing for title: Marketing Coordinator
Completed processing for title: Marketing Specialist
Completed processing for title: Content Marketing Manager
Completed processing for title: Digital Marketing Specialist
Completed processing for title: SEO Specialist
Completed processing for title: Social Media Manager
Completed processing for title: Brand Manager
Completed processing for title: Product Marketing Manager
Completed processing for title: Marketing
Completed processing for title: Search Planner
All searches and updates completed.


In [176]:
Scientific_Research_list = [
    'Research Scientist', 'Biologist', 'Chemist', 'Physicist', 'Sterilization', 'Cytotechnologist', 'Specimen',
    'Data Scientist', 'Lab Technician', 'Biomedical Scientist', 'Behavior Technician',
    'Clinical Research Coordinator', 'Research Associate', 'Research Fellow', 'Ecologist', 'Lab', 'Laboratory', 'Scientist', 'Molecules',
]

for title in Scientific_Research_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Research'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'R&D' and subcategory to 'Research'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'R&D',
                            'subcategory': 'Research'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


Completed processing for title: Research Scientist
Completed processing for title: Biologist


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\2693072036.py:10: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Chemist
Completed processing for title: Physicist
Completed processing for title: Sterilization
Completed processing for title: Cytotechnologist
Completed processing for title: Specimen
Completed processing for title: Data Scientist
Completed processing for title: Lab Technician
Completed processing for title: Biomedical Scientist
Completed processing for title: Behavior Technician
Completed processing for title: Clinical Research Coordinator
Completed processing for title: Research Associate
Completed processing for title: Research Fellow
Completed processing for title: Ecologist
Completed processing for title: Lab
Completed processing for title: Laboratory
Completed processing for title: Scientist
Completed processing for title: Molecules
All searches and updates completed.


In [177]:
Scientific_Development_list = [
    'Scientific Developer', 'Bioinformatics Specialist', 'Pharmaceutical Scientist', 
    'Research and Development (R&D) Scientist', 'Engineering Scientist', 
    'Technical Research Scientist', 'Scientific Programmer', 
    'Process Development Scientist', 'Applied Scientist', 'Development Chemist', 'Hazardous Waste Technician'
]

for title in Scientific_Development_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'subcategory': 'Development'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'R&D' and subcategory to 'Development'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'R&D',
                            'subcategory': 'Development'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


Completed processing for title: Scientific Developer
Completed processing for title: Bioinformatics Specialist
Completed processing for title: Pharmaceutical Scientist
Completed processing for title: Research and Development (R&D) Scientist
Completed processing for title: Engineering Scientist
Completed processing for title: Technical Research Scientist
Completed processing for title: Scientific Programmer
Completed processing for title: Process Development Scientist


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\627140862.py:11: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Applied Scientist
Completed processing for title: Development Chemist
Completed processing for title: Hazardous Waste Technician
All searches and updates completed.


In [178]:
Finance_list = [
    'Financial Analyst', 'Financial Manager', 'Investment Banker', 'Accounting', 'Finance',
    'Accountant', 'Financial Advisor', 'Treasury Analyst', 
    'Credit Analyst', 'Finance Director', 'Portfolio Manager', 'Fico', 'Wealth Advisor',
    'Risk Manager', 'Tax Advisor', 'Controller', 'Auditor', 'Bookkeeper',
    'Corporate Finance Analyst', 'Finance Associate', 'Broker', 'Brokerage', 'Banker', 'Accounts Payable', 'Financial Planning', 'Teller', 'Wealth Mananger'
]

for title in Finance_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Finance'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Finance' and subcategory to 'Unknown'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Finance',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


Completed processing for title: Financial Analyst


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1492102583.py:12: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Financial Manager
Completed processing for title: Investment Banker
Completed processing for title: Accounting
Completed processing for title: Finance
Completed processing for title: Accountant
Completed processing for title: Financial Advisor
Completed processing for title: Treasury Analyst
Completed processing for title: Credit Analyst
Completed processing for title: Finance Director
Completed processing for title: Portfolio Manager
Completed processing for title: Fico
Completed processing for title: Wealth Advisor
Completed processing for title: Risk Manager
Completed processing for title: Tax Advisor
Completed processing for title: Controller
Completed processing for title: Auditor
Completed processing for title: Bookkeeper
Completed processing for title: Corporate Finance Analyst
Completed processing for title: Finance Associate
Completed processing for title: Broker
Completed processing for title: Brokerage
Completed processing for title: Banker
Co

In [179]:
Retail_list = [
    'Retail Sales Associate', 'Retail Manager', 'Store Manager', 'retail', 'Store ', 'stockkeeper',
    'Assistant Store Manager', 'Sales Floor Associate', 'Customer Service Representative', 'Merchandiser',
    'Visual Merchandiser', 'Inventory Manager', 'Retail Buyer', 'Cashier', 
    'Stock Clerk', 'Department Manager', 'Retail Sales Supervisor', 'Merchandising Associate',
    'Loss Prevention Specialist', 'E-commerce Specialist', 'Stock Associate', 'Store Fulfillment', 'Retail Merchandise Processor'
]

for title in Retail_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Retail'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Check if we received a valid scroll ID
        if '_scroll_id' not in result:
            print(f"No scroll ID returned for title '{title}'")
            continue
        
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Retail'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Retail',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1571190280.py:12: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


Completed processing for title: Retail Sales Associate
Completed processing for title: Retail Manager
Completed processing for title: Store Manager
Completed processing for title: retail
Completed processing for title: Store 
Completed processing for title: stockkeeper
Completed processing for title: Assistant Store Manager
Completed processing for title: Sales Floor Associate
Completed processing for title: Customer Service Representative
Completed processing for title: Merchandiser
Completed processing for title: Visual Merchandiser
Completed processing for title: Inventory Manager
Completed processing for title: Retail Buyer
Completed processing for title: Cashier
Completed processing for title: Stock Clerk
Completed processing for title: Department Manager
Completed processing for title: Retail Sales Supervisor
Completed processing for title: Merchandising Associate
Completed processing for title: Loss Prevention Specialist
Completed processing for title: E-commerce Specialist
Comp

In [180]:
Food_Industry_list = [
    'Chef', 'Cook', 'Restaurant Manager', 'Sous Chef', 
    'Pastry Chef', 'Food Service Manager', 'Food and Beverage Director', 
    'Barista', 'Baker', 'Line Cook', 'Food Prep Worker', 
    'Dishwasher', 'Catering Manager', 'Food Safety Specialist', 'Nutritionist', 'Claims Service'
]

for title in Food_Industry_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Food Industry'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Food Industry'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Food Industry',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1752395283.py:11: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [181]:
Entertainment_list = [
    'Actor', 'Director', 'Producer', 'Screenwriter', 
    'Cinematographer', 'Film Editor', 'Production Assistant', 
    'Lighting Technician', 'Sound Engineer', 'Costume Designer', 
    'Makeup Artist', 'Talent Agent', 'Event Coordinator', 
    'Music Producer', 'Stage Manager', 'Set Designer', 
    'Script Supervisor', 'Voice Actor', 'Film Critic',
    'Game Designer', 'Game Developer', 'Game Programmer', 
    'Game Artist', 'Game Animator', 'Game Tester', 
    'Level Designer', 'Narrative Designer', 'UX/UI Designer (Gaming)', 
    'Game Producer', 'Sound Designer (Gaming)',
    'Visual Artist', 'Graphic Designer', 'Illustrator', 
    'Art Director', 'Concept Artist', 'Animator', 
    '3D Modeler', 'Storyboard Artist', 'Digital Painter', 
    'Printmaker', 'Art Curator', 'Exhibition Organizer',
    'Composer', 'Musician', 'Music Director', 'Vocal Coach',
    'Sound Technician', 'Music Arranger', 'Music Educator', 
    'Live Sound Engineer', 'Music Therapist', 'Songwriter',
    'Music Supervisor', 'Audio Engineer', 'Music Producer',
    'Author', 'Novelist', 'Copywriter', 'Technical Writer',
    'Content Writer', 'Editorial Writer', 'Blogger', 
    'Creative Writer', 'Ghostwriter', 'Research Writer',
    'Scriptwriter', 'Playwright', 'Editor', 'writer'
]

for title in Entertainment_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Entertainment'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Entertainment'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Entertainment',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\997366828.py:29: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [182]:
Education_list = [
    # Teachers
    'Teacher', 'Classroom Teacher', 'Elementary School Teacher', 'Tutor', 'Trainer',
    'High School Teacher', 'Middle School Teacher', 
    'Special Education Teacher', 'Language Arts Teacher', 'Campus', 'School', 'Dean',
    'Math Teacher', 'Science Teacher', 'History Teacher', 
    'Physical Education Teacher', 'Art Teacher', 'Music Teacher', "Education", 'Educator', 'Coach', 'instructor', 'Pastor', 'preist', 'Church',
    
    # Administrators
    'Principal', 'Vice Principal', 'School Administrator', 
    'School Counselor', 'Dean of Students', 'Registrar', 
    'Director of Curriculum', 'Educational Coordinator', 
    'Educational Consultant',
    
    # Support Staff
    "Teacher's Aide", 'Special Education Aide', 
    'Administrative Assistant', 'School Nurse', 'School Librarian', 
    'Guidance Counselor', 'Educational Therapist',
    
    # Higher Education
    'Professor', 'Associate Professor', 'Assistant Professor', 
    'Lecturer', 'Researcher', 'Dean of Faculty', 
    'Academic Advisor', 'Admissions Counselor', 
    'University Administrator', 'Provost',
    
    # Training and Development
    'Learning and Development Manager'
]

for title in Education_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Education'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Education'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Education',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\101859213.py:33: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [183]:
Police_Security_list = [
    # Police Jobs
    'Police Officer', 'Detective', 'Sergeant', 'Lieutenant', 
    'Captain', 'Chief of Police', 'Criminal Investigator', 
    'Patrol Officer', 'K9 Officer', 'SWAT Team Member', 
    'Traffic Officer', 'School Resource Officer', 
    'Forensic Specialist', 'Crime Scene Investigator', 
    'Police Dispatcher',
    
    # Security Jobs
    'Security Guard', 'Security Officer', 'Loss Prevention Specialist', 
    'Security Manager', 'Security Supervisor', 'Armed Security Officer', 
    'Unarmed Security Officer', 'Event Security', 'Corporate Security', 
    'Private Investigator', 'Security Consultant', 
    'Security Systems Technician', 'CCTV Operator', 
    'Access Control Specialist', 'Risk Assessment Analyst', 'Events Security'
]

for title in Police_Security_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Police and Security'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Police and Security'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Police and Security',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\933306983.py:22: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [184]:
Legal_list = [
    # Attorneys and Lawyers
    'Attorney', 'Lawyer', 'Criminal Defense Attorney', 
    'Corporate Lawyer', 'Family Lawyer', 'Immigration Lawyer', 
    'Personal Injury Lawyer', 'Real Estate Lawyer', 'Tax Lawyer', 
    'Environmental Lawyer', 'Investigator', 'Legislative', 'Actuary', 'Actual', 'Actuarial',
    
    # Legal Support
    'Paralegal', 'Legal Assistant', 'Legal Secretary', 
    'Legal Researcher', 'Court Clerk', 'Legal Document Specialist', 
    'Legal Transcriptionist',
    
    # Judiciary
    'Judge', 'Magistrate', 'Hearing Officer', 'Court Administrator',
    
    # Compliance and Risk Management
    'Compliance Officer', 'Risk Manager', 'Compliance Analyst', 
    'Regulatory Affairs Specialist',
    
    # Legal Consulting
    'Legal Consultant', 'Contract Manager', 'Legal Advisor', 
    'Mediation Specialist', 'Arbitration Specialist', 'Tax'
]

for title in Legal_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Legal'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Legal'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Legal',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1217386733.py:28: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [185]:
Skilled_trade_list = [
    'Electrician',
    'Plumber',
    'Carpenter',
    'Mason',
    'Roofer', 'Repair',
    'Drywaller', 'Stylist',
    'HVAC Technician',
    'Automotive Mechanic', 'Home Technician', 'Forklift',
    'Diesel Mechanic',
    'Industrial Machinery Mechanic', 'Designer', 
    'Welder',
    'Machinist',
    'CNC Operator',
    'Elevator Installer', 'Installer', 'Pest', 'Roofing', 'Automotive Technician',
    'Boilermaker',
    'Pipefitter',
    'Glassblower', 'Civil Structural Designer',
    'Jeweler', 'Fabricator',
    'Stone Carver', 'Operations', 'Designer',
    'Landscape Architect',
    'Insulation Installer', 'Artisan Fitter',
    'Sign Maker',
    'Mechanic', 'Maintenance', 'Operator', 'Gas Fitter', 'Hairdresser', 'Barber', 'Valve Technician', 'Service Technician'
]

for title in Skilled_trade_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Skilled Trade'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Skilled Trade'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Skilled Trade',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\4063466519.py:30: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [ ]:
General_management_list = ['Lead', 'recruiter', 'Recruiting', 'Manager', 'Superintendent', 'Team Leader', 'Quality Assurance', 'Quality Control']

for title in General_management_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Management'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Management'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Management',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


In [186]:
Labor_list = [
    'Construction Laborer', 'Laborer', 'Dashers',
    'Demolition Worker',
    'Production Line Worker',
    'Packager',
    'Janitor', 'Custodian',
    'Housekeeper',
    'Cashier',
    'Stock Clerk', 'Cleaner', 'Shipper',
    'Farm Laborer',
    'Landscaping Laborer', 'Production', 'Dispatcher', 
    'Warehouse Worker',
    'Loader', 'Drive', 'dasher', 'Delivery', 
    'Delivery Helper',
    'Attendant', 'warehouse', 'Assembler',
    'Set-Up Crew',
    'Housekeeping', 'Mine', 'Manufacturing', 'Housekeeper', 'Driver', 'Hosts'
]

for title in Labor_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Labor'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Labor'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Labor',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\2560462480.py:23: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [187]:
Service_list = [
    'Customer Service Representative',
    'Call Center Agent',
    'Client Relations Specialist', 'Vehicle Service Agent', 'Customer Experience',
    'Concierge',
    'Travel Agent',
    'Store Manager',
    'Cashier',
    'Waiter', 'Service Coordinator', 'Customer Executive',
    'Field Service', 'hospitality',
    'Personal Trainer',
    'Massage Therapist', 'Customer Relations',
    'Consultant',
    'Financial Advisor', 'Beauty Advisor', 'Client Service', 'Servicing Customer Care',
    'Social Worker',
    'Community Outreach Coordinator',
    'Case Manager', 'Child Protection', 'Server', 'Fan Services', 'Customer Service'
]

for title in Service_list:
    try:
        # Perform initial search with scroll parameter
        result = es.search(
            index='jobs_prd_filtered',
            body={
                "query": {
                    "bool": {
                        "must": {
                            "match_phrase": {'title': title}
                        },
                        "must_not": {
                            "match_phrase": {'category': 'Service'}
                        }
                    }
                }
            },
            scroll='2m',  # Keep the search context open for 2 minutes
            size=1000      # Number of documents per batch
        )

        # Use the scroll ID from the initial search response
        scroll_id = result['_scroll_id']
        hits = result['hits']['hits']

        while hits:
            for hit in hits:
                document_id = hit['_id']
                # Update the document to set the category to 'Service'
                es.update(
                    index='jobs_prd_filtered', 
                    id=document_id, 
                    body={
                        'doc': {
                            'category': 'Service',
                            'subcategory': 'Unknown'
                        }
                    }
                )
            
            # Fetch the next batch of results using the scroll ID
            result = es.scroll(
                scroll_id=scroll_id, 
                scroll='2m'  # Continue using the same scroll context for 2 minutes
            )
            hits = result['hits']['hits']
        
        # Clear the scroll context to free up resources
        es.clear_scroll(scroll_id=scroll_id)

        # Optional: Print a completion message for each title
        #print(f"Completed processing for title: {title}")

    except Exception as e:
        print(f"An error occurred for title '{title}': {e}")

print("All searches and updates completed.")

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\918037236.py:23: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  result = es.search(


All searches and updates completed.


In [ ]:
#END OF FILTERED CATEGORIES

In [ ]:
#CREATING JOBS_HEALTH_FILTERED INDEX------------------------------------------------------------

In [188]:
es.indices.delete(index = "jobs_health_filtered")

ObjectApiResponse({'acknowledged': True})

In [189]:
#Define mapping of 'jobs_health_filtered'

mapping = {
    "mappings": {
        "properties": {
            "category": {
                "type": "keyword"
            },
            "region": {
                "type": "keyword"
            },
            "month": {
                "type": "date",
                "format": "yyyy-MM-dd'T'HH:mm:ss"
            },
            "month_text": {
                "type": "keyword"
            },
            "total_entries": {
                "type": "integer" 
            },
            "average_salary": {
                "type": "float" 
            },
            "timestamp": {
                "type": "date", 
                "format": "yyyy-MM-dd'T'HH:mm:ss.SSSSSS"
            },
            "diff": {
                "type": "float" 
            },
            "diff_percentage": {
                "type": "float" 
            },
            "overall_average_salary": {
                "type": "float" 

            },
            "score" : {
                "type": "float" 

            },
            "status": {
                "type": "keyword" 
            }
        }
    }
}

# Create the index with the defined mapping
es.indices.create(index='jobs_health_filtered', body=mapping, ignore=400) 


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\433896934.py:51: DeprecationWarning: Passing transport options in the API method is deprecated. Use 'Elasticsearch.options()' instead.
  es.indices.create(index='jobs_health_filtered', body=mapping, ignore=400)


ObjectApiResponse({'acknowledged': True, 'shards_acknowledged': True, 'index': 'jobs_health_filtered'})

In [190]:
#Tier1 METRICS SALARY COUNT, AVERAGE, AND OVERALL AVERAGE SALARY for FILTERED

import time
from datetime import datetime
from elasticsearch import Elasticsearch
from elasticsearch.helpers import bulk

def fetch_and_index_data():
    start = time.time()
    current_time = datetime.now()
    timestamp_str = current_time.isoformat()

    print(timestamp_str)
    print('Start time: ' + str(current_time))

    body = {
        "size": 0,  # No need to return the actual documents
        "aggs": {
            "by_region": {
                "terms": {
                    "field": "region.keyword",
                    "size": 10
                },
                "aggs": {
                    "by_category": {
                        "terms": {
                            "field": "category.keyword",
                            "size": 10
                        },
                        "aggs": {
                            "by_month": {
                                "terms": {
                                    "field": "post_month.keyword",
                                    "size": 12
                                },
                                "aggs": {
                                    "total_entries": {
                                        "value_count": {
                                            "field": "post_month.keyword"
                                        }
                                    },
                                    "average_salary": {
                                        "avg": {
                                            "field": "yearly_salary"
                                        }
                                    }
                                }
                            },
                            # New aggregation for overall average salary
                            "overall_average_salary": {
                                "avg_bucket": {
                                    "buckets_path": "by_month>average_salary"
                                }
                            }
                        }
                    }
                }
            }
        }
    }

    # Execute the search with aggregation
    response = es.search(index='jobs_prd_filtered', body=body)
    print("Aggregation response:", response)  # Debugging output

    actions = []
    for region_bucket in response['aggregations']['by_region']['buckets']:
        region = region_bucket['key']
        for category_bucket in region_bucket['by_category']['buckets']:
            category = category_bucket['key']
            # Calculate overall average salary across all months
            overall_average_salary = category_bucket['overall_average_salary']['value']
            if overall_average_salary is None:
                overall_average_salary = 0.0
            else:
                overall_average_salary = "{:.2f}".format(overall_average_salary)
            for month_bucket in category_bucket['by_month']['buckets']:
                monthword = month_bucket['key']
                try:
                    month = datetime.strptime(monthword, "%B %Y").isoformat()
                except ValueError:
                    month = None  # Handle parsing errors if month format is not as expected
                
                total_entries = month_bucket['total_entries']['value']
                average_salary = month_bucket['average_salary']['value']
                
                if average_salary is None:
                    average_salary = 0.0
                else:
                    average_salary = "{:.2f}".format(average_salary)
                
                # Prepare document for bulk indexing
                doc = {
                    'region': region,
                    'category': category,
                    'month_text': monthword,
                    'month': month,
                    'total_entries': total_entries,
                    'average_salary': average_salary,
                    'overall_average_salary': overall_average_salary,
                    'timestamp': timestamp_str
                }
                
                actions.append({
                    "_op_type": "index",
                    "_index": "jobs_health_filtered",
                    "_source": doc
                })
            
    # Perform bulk indexing
    try:
        if actions:
            response = bulk(es, actions)
            print(f"Bulk indexed {response[0]} documents into 'jobs_health_filtered'.")
        else:
            print("No actions to index.")
    except Exception as e:
        print(f"An error occurred during bulk indexing: {e}")

    print('Elapsed run time: ' + str(time.time() - start))

if __name__ == "__main__":
    fetch_and_index_data()


2024-09-16T16:08:17.636163
Start time: 2024-09-16 16:08:17.636163
Aggregation response: {'took': 31, 'timed_out': False, '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0}, 'hits': {'total': {'value': 10000, 'relation': 'gte'}, 'max_score': None, 'hits': []}, 'aggregations': {'by_region': {'doc_count_error_upper_bound': 0, 'sum_other_doc_count': 0, 'buckets': [{'key': 'Southeast', 'doc_count': 29151, 'by_category': {'doc_count_error_upper_bound': 0, 'sum_other_doc_count': 3645, 'buckets': [{'key': 'Unknown', 'doc_count': 8306, 'by_month': {'doc_count_error_upper_bound': 0, 'sum_other_doc_count': 0, 'buckets': [{'key': 'April 2024', 'doc_count': 8208, 'total_entries': {'value': 8208}, 'average_salary': {'value': 187895.9714859836}}, {'key': 'March 2024', 'doc_count': 97, 'total_entries': {'value': 97}, 'average_salary': {'value': 80469.29411764706}}, {'key': 'February 2024', 'doc_count': 1, 'total_entries': {'value': 1}, 'average_salary': {'value': None}}]}, 'overall_av

In [191]:
#Teir2 - diff 

def update_diff_field():
    """
    Update the 'diff' field in all documents in the 'jobs_health_filtered' index.
    The 'diff' field is calculated as 'average_salary' - 'overall_average_salary'.
    """
    # Define the query to fetch all documents that have 'overall_average_salary' and 'average_salary' fields
    query = {
        "query": {
            "bool": {
                "must": [
                    {"exists": {"field": "overall_average_salary"}},
                    {"exists": {"field": "average_salary"}}
                ]
            }
        },
        "_source": ["overall_average_salary", "average_salary"]
    }
    
    # Initialize scroll
    search_result = es.search(index='jobs_health_filtered', body=query, scroll='2m', size=1000)
    
    scroll_id = search_result['_scroll_id']
    hits = search_result['hits']['hits']
    
    actions = []
    
    while hits:
        for hit in hits:
            doc_id = hit['_id']
            doc_source = hit['_source']
            
            overall_average_salary = doc_source.get('overall_average_salary')
            average_salary = doc_source.get('average_salary')
            
            if overall_average_salary is not None and average_salary is not None:
                diff = float(average_salary) - float(overall_average_salary)

                update_body = {
                    "doc": {
                        "diff": round(diff, 2)
                    }
                }

                actions.append({
                    "_op_type": "update",
                    "_index": "jobs_health_filtered",
                    "_id": doc_id,
                    **update_body
                })

        # Fetch the next batch of results
        search_result = es.scroll(scroll_id=scroll_id, scroll='2m')
        hits = search_result['hits']['hits']
    
    # Perform bulk update
    try:
        if actions:
            bulk(es, actions)
            print(f"Bulk updated {len(actions)} documents in 'jobs_health_filtered'.")
        else:
            print("No documents were updated.")
    except Exception as e:
        print(f"An error occurred during bulk update: {e}")

def main():
    start = time.time()

    print('Start time: ' + str(datetime.now()))

    update_diff_field()

    print('Elapsed run time: ' + str(time.time() - start))

if __name__ == "__main__":
    main()


Start time: 2024-09-16 16:09:43.475419
Bulk updated 134 documents in 'jobs_health_filtered'.
Elapsed run time: 0.0408625602722168


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\367732319.py:22: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  search_result = es.search(index='jobs_health_filtered', body=query, scroll='2m', size=1000)


In [192]:
#Teir2 - diff_percentage for FILTERED
def update_diff_percentage_field():
    """
    Update the 'diff_percentage' field in all documents in the 'jobs_health_filtered' index.
    The 'diff_percentage' field is calculated as 'diff' / 'overall_average_salary'.
    """
    # Define the query to fetch all documents that have 'diff' and 'overall_average_salary' fields
    query = {
        "query": {
            "bool": {
                "must": [
                    {"exists": {"field": "diff"}},
                    {"exists": {"field": "overall_average_salary"}}
                ]
            }
        },
        "_source": ["diff", "overall_average_salary"]
    }
    
    # Initialize scroll
    search_result = es.search(index='jobs_health_filtered', body=query, scroll='2m', size=1000)
    
    scroll_id = search_result['_scroll_id']
    hits = search_result['hits']['hits']
    
    actions = []
    
    while hits:
        for hit in hits:
            doc_id = hit['_id']
            doc_source = hit['_source']
            
            diff = doc_source.get('diff')
            overall_average_salary = float(doc_source.get('overall_average_salary'))
            
            if overall_average_salary and overall_average_salary != 0:
                diff_percentage = diff / overall_average_salary

                update_body = {
                    "doc": {
                        "diff_percentage": round(diff_percentage, 4)
                    }
                }

                actions.append({
                    "_op_type": "update",
                    "_index": "jobs_health_filtered",
                    "_id": doc_id,
                    **update_body
                })

        # Fetch the next batch of results
        search_result = es.scroll(scroll_id=scroll_id, scroll='2m')
        hits = search_result['hits']['hits']
    
    # Perform bulk update
    try:
        if actions:
            bulk(es, actions)
            print(f"Bulk updated {len(actions)} documents in 'jobs_health_filtered'.")
        else:
            print("No documents were updated.")
    except Exception as e:
        print(f"An error occurred during bulk update: {e}")

def main():
    start = time.time()

    print('Start time: ' + str(datetime.now()))

    update_diff_percentage_field()

    print('Elapsed run time: ' + str(time.time() - start))

if __name__ == "__main__":
    main()


Start time: 2024-09-16 16:09:45.279929
Bulk updated 134 documents in 'jobs_health_filtered'.
Elapsed run time: 0.03289055824279785


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\1684327578.py:21: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  search_result = es.search(index='jobs_health_filtered', body=query, scroll='2m', size=1000)


In [193]:
# Metrics Tier 2- score and status for FILTERED

def update_score_and_status_field():
    """
    Update the 'score' and 'status' fields in all documents in the 'jobs_health_filtered' index.
    The 'score' and 'status' fields are calculated based on the 'diff' field.
    """
    # Define the query to fetch all documents that have 'diff' field
    query = {
        "query": {
            "exists": {
                "field": "diff"
            }
        },
        "_source": ["diff"]
    }
    
    # Initialize scroll
    search_result = es.search(index='jobs_health_filtered', body=query, scroll='2m', size=1000)
    
    scroll_id = search_result['_scroll_id']
    hits = search_result['hits']['hits']
    
    actions = []
    
    while hits:
        for hit in hits:
            doc_id = hit['_id']
            doc_source = hit['_source']
            
            diff = doc_source.get('diff')
            
            if diff is not None:
                # Calculate score and status
                if diff > 0:
                    score = 1
                    status = "UP"
                elif diff == 0:
                    score = 0
                    status = "UNCHG"
                else:
                    score = -1
                    status = "DOWN"
                
                update_body = {
                    "doc": {
                        "score": score,
                        "status": status
                    }
                }

                actions.append({
                    "_op_type": "update",
                    "_index": "jobs_health_filtered",
                    "_id": doc_id,
                    **update_body
                })

        # Fetch the next batch of results
        search_result = es.scroll(scroll_id=scroll_id, scroll='2m')
        hits = search_result['hits']['hits']
    
    # Perform bulk update
    try:
        if actions:
            bulk(es, actions)
            print(f"Bulk updated {len(actions)} documents in 'jobs_health_filtered'.")
        else:
            print("No documents were updated.")
    except Exception as e:
        print(f"An error occurred during bulk update: {e}")

def main():
    start = time.time()

    print('Start time: ' + str(datetime.now()))

    update_score_and_status_field()

    print('Elapsed run time: ' + str(time.time() - start))

if __name__ == "__main__":
    main()


Start time: 2024-09-16 16:09:47.083151
Bulk updated 134 documents in 'jobs_health_filtered'.
Elapsed run time: 0.02790999412536621


C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\765616381.py:19: DeprecationWarning: Received 'size' via a specific parameter in the presence of a 'body' parameter, which is deprecated and will be removed in a future version. Instead, use only 'body' or only specific parameters.
  search_result = es.search(index='jobs_health_filtered', body=query, scroll='2m', size=1000)


In [194]:
# Metrics Tier 3 - OVERALL SCORE BASED ON WEIGHTS
# Regional weights
regional_weights = {
    "Southeast": 1.1,
    "Northeast": 1.0,
    "Midwest": 0.8,
    "West": 0.7,
    "Southwest": 0.6,
    "Remote": 0.5
}

def calculate_region_scores_for_month(month_text):
    """
    Calculate the average score for each region for a given month_text.
    """
    region_scores = {}
    
    # Fetch average score for each region for the given month_text
    query = {
        "query": {
            "bool": {
                "must": [
                    {"match": {"month_text": month_text}}
                ]
            }
        },
        "aggs": {
            "by_region": {
                "terms": {
                    "field": "region",
                    "size": len(regional_weights)  # Ensure to include all possible regions
                },
                "aggs": {
                    "average_score": {
                        "avg": {
                            "field": "score"
                        }
                    }
                }
            }
        }
    }
    
    response = es.search(index='jobs_health_filtered', body=query)
    
    # Process region buckets
    region_buckets = response['aggregations']['by_region']['buckets']
    
    for region_bucket in region_buckets:
        region = region_bucket['key']
        avg_score = region_bucket['average_score']['value']
        print(avg_score, region)
        if avg_score is not None:
            region_scores[region] = avg_score
    
    return region_scores

def calculate_overall_score(region_scores):
    """
    Calculate the overall score based on regional scores and weights.
    """
    weighted_score_sum = 0
    total_weight = 0
    
    for region, score in region_scores.items():
        weight = regional_weights.get(region, 0)
        weighted_score_sum += score * weight
        total_weight += weight
    
    if total_weight > 0:
        overall_score = weighted_score_sum / total_weight
    else:
        overall_score = 0
    
    return overall_score

def insert_overall_score(month_text, overall_score, timestamp):
    """
    Insert a new document into 'jobs_health' with the calculated overall_score.
    """
    doc = {
        "region": "USA",
        "category": "All",
        "month_text": month_text,
        "score": overall_score,
        "timestamp": timestamp
    }
    
    try:
        res = es.index(index='jobs_health_filtered', document=doc)
        print(f"Inserted document for month '{month_text}' with score: {overall_score}")
    except Exception as e:
        print(f"An error occurred during document insertion: {e}")

def process_monthly_scores(start_time):
    """
    Process each unique month_text, calculate the regional scores, overall score, and insert the result.
    """
    # Fetch unique month_text values
    query = {
        "aggs": {
            "unique_months": {
                "terms": {
                    "field": "month_text",
                    "size": 1000  # Adjust size if needed
                }
            }
        }
    }
    
    response = es.search(index='jobs_health_filtered', body=query)
    #print(response)
    # Process month buckets
    month_buckets = response['aggregations']['unique_months']['buckets']
    #print(month_buckets)
    
    for month_bucket in month_buckets:
        month_text = month_bucket['key']
        print('Month_text:', month_text)
        # Calculate region scores for this month_text
        region_scores = calculate_region_scores_for_month(month_text)
        print('region_scores:', region_scores)
        # Calculate overall score
        overall_score = calculate_overall_score(region_scores)
        print('overall_score:', overall_score)
        # Insert the overall score into the index
        insert_overall_score(month_text, overall_score, start_time)

def main():
    start_time = datetime.utcnow().strftime('%Y-%m-%dT%H:%M:%S.%f')  # Use UTC format and include microseconds
    start = time.time()
    print(f"Start time: {start_time}")
    
    # Process monthly scores
    process_monthly_scores(start_time)
    
    print(f'Elapsed run time: {time.time() - start:.2f} seconds')

if __name__ == "__main__":
    main()



Start time: 2024-09-16T20:09:49.356178
Month_text: April 2024
0.1 Midwest
0.0 Northeast
-0.3 Remote
0.0 Southeast
0.1 Southwest
-0.2 West
region_scores: {'Midwest': 0.1, 'Northeast': 0.0, 'Remote': -0.3, 'Southeast': 0.0, 'Southwest': 0.1, 'West': -0.2}
overall_score: -0.03191489361702127
Inserted document for month 'April 2024' with score: -0.03191489361702127
Month_text: March 2024
-0.2 Midwest
0.4 Northeast
0.4 Remote
0.0 Southeast
-0.2 Southwest
0.2 West
region_scores: {'Midwest': -0.2, 'Northeast': 0.4, 'Remote': 0.4, 'Southeast': 0.0, 'Southwest': -0.2, 'West': 0.2}
overall_score: 0.0978723404255319
Inserted document for month 'March 2024' with score: 0.0978723404255319
Month_text: February 2024
-1.0 Northeast
-1.0 Southeast
-1.0 West
-1.0 Remote
region_scores: {'Northeast': -1.0, 'Southeast': -1.0, 'West': -1.0, 'Remote': -1.0}
overall_score: -1.0
Inserted document for month 'February 2024' with score: -1.0
Month_text: January 2024
-1.0 Midwest
-1.0 Northeast
-1.0 Remote
-1.0 So

C:\Users\vicyu\AppData\Local\Temp\ipykernel_3572\2920750791.py:130: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  start_time = datetime.utcnow().strftime('%Y-%m-%dT%H:%M:%S.%f')  # Use UTC format and include microseconds
